<a href="https://colab.research.google.com/github/DragonFarts/Goosey-Gui/blob/main/Goosey_GUI_v0_05.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# STEP 1 - Install

In [ ]:
%cd /content
!mkdir /content/input_vid
!mkdir /content/input_immg
!git lfs install
!git clone https://huggingface.co/spaces/diffusers/unofficial-SDXL-Turbo-i2i-t2i
!pip install -r /content/unofficial-SDXL-Turbo-i2i-t2i/requirements.txt
%cd /content
!git clone -b dev https://github.com/camenduru/background-replacement-hf
%cd /content/background-replacement-hf
!pip install -q -r requirements.txt

!wget https://github.com/camenduru/background-replacement-hf/assets/54370274/aee10271-04e5-4ea8-94d7-9717e73dd4a2 -O /content/background-replacement-hf/examples/dj-making-music-on-mixer.jpg
!wget https://github.com/camenduru/background-replacement-hf/assets/54370274/663da768-22b6-4ccb-bbd1-744ded312063 -O /content/background-replacement-hf/examples/jean-shorts-woman.jpg
!wget https://github.com/camenduru/background-replacement-hf/assets/54370274/122b89e5-c1d2-46d9-aa90-56a41e916b19 -O /content/background-replacement-hf/examples/black-sneakers-with-white-sole.jpg
!wget https://github.com/camenduru/background-replacement-hf/assets/54370274/d8c15c10-cef2-4a92-9d66-0fd34caf1213 -O /content/background-replacement-hf/examples/DIY-beard-balm.jpg
%cd /content
!pip install flask
!pip install pyngrok
!npm install -g localtunnel

/content
Git LFS initialized.
Cloning into 'unofficial-SDXL-Turbo-i2i-t2i'...
remote: Enumerating objects: 34, done.
remote: Counting objects: 100% (25/25), done.
remote: Compressing objects: 100% (24/24), done.
remote: Total 34 (delta 14), reused 1 (delta 1), pack-reused 9
Unpacking objects: 100% (34/34), 6.44 KiB | 733.00 KiB/s, done.
Looking in indexes: https://pypi.org/simple, https://download.pytorch.org/whl/cu121
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 24.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.5/16.5 MB 62.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.9/92.9 kB 14.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.5/59.5 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 98.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.0/261.0 kB 31.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 202.4/202.4 kB 29.3 MB/s eta 0:00:00
  Preparing

/content
Cloning into 'background-replacement-hf'...
remote: Enumerating objects: 69, done.
remote: Counting objects: 100% (69/69), done.
remote: Compressing objects: 100% (51/51), done.
remote: Total 69 (delta 32), reused 43 (delta 16), pack-reused 0
Receiving objects: 100% (69/69), 28.43 KiB | 9.48 MiB/s, done.
Resolving deltas: 100% (32/32), done.
Error downloading object: examples/DIY-beard-balm.jpg (8b05f7f): Smudge error: Error downloading examples/DIY-beard-balm.jpg (8b05f7fad89d7bafc1f58cf154b7948690817058adbca636c6b45c658d3cd312): [8b05f7fad89d7bafc1f58cf154b7948690817058adbca636c6b45c658d3cd312] Object does not exist on the server: [404] Object does not exist on the server

Errors logged to /content/background-replacement-hf/.git/lfs/logs/20231230T225732.504955722.log
Use `git lfs logs last` to view the log.
error: external filter 'git-lfs filter-process' failed
fatal: examples/DIY-beard-balm.jpg: smudge filter lfs failed
You can inspect what was checked out with 'git status'

In [ ]:
%%writefile /content/background-replacement-hf/removebg.py
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)
warnings.filterwarnings("ignore", category=UserWarning)
import os
import sys
from PIL import Image
import torch
from tqdm import tqdm
from background_replacer import replace_background

# Initialize the components (assuming the necessary initializations are in the imported modules)
from captioner import init as init_captioner
from upscaler import init as init_upscaler
from segmenter import init as init_segmenter
from depth_estimator import init as init_depth_estimator
from pipeline import init as init_pipeline

def main(input_path, output_path):
    init_captioner()
    init_upscaler()
    init_segmenter()
    init_depth_estimator()
    init_pipeline()

    # Clear any cached data in PyTorch
    torch.cuda.empty_cache()

    # Environment variable to toggle developer mode
    developer_mode = True  # Set this to False if needed

    # Default prompts for background replacement
    DEFAULT_POSITIVE_PROMPT = "on the pavement, poolside, idyllic infinity pool, Hawaiian hilltops, commercial product photography"
    DEFAULT_NEGATIVE_PROMPT = ""

    # Set default values for options
    options = {
        'seed': 0,
        'depth_map_feather_threshold': 128,
        'depth_map_dilation_iterations': 10,
        'depth_map_blur_radius': 10,
    }

    # Load an image
    original_image = Image.open(input_path)

    # Call the replace_background function
    result = replace_background(
        original_image,
        DEFAULT_POSITIVE_PROMPT,
        DEFAULT_NEGATIVE_PROMPT,
        options
    )

    # Handling the result
    if result is not None and isinstance(result, list) and developer_mode:
        pre_processing_images = result[2]  # List of preprocessing images
        for item in pre_processing_images:
            img, label = item
            if label == "Cropped":
                img.save(output_path)
                break
        print("Cropped image saved to:", output_path)
    else:
        print("No result was generated or developer mode is off.")

if __name__ == "__main__":
    if len(sys.argv) != 3:
        print("Usage: python removebg.py <input_path> <output_path>")
        sys.exit(1)

    input_path = sys.argv[1]
    output_path = sys.argv[2]
    main(input_path, output_path)


Writing /content/background-replacement-hf/removebg.py


In [ ]:
#!pip uninstall torch torchvision torchaudio -y
#!pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118
#!pip uninstall xformers transformers -y
#!pip install xformers transformers

In [ ]:
import torch
from diffusers import AutoPipelineForText2Image, AutoPipelineForImage2Image
# Initialize the text-to-image pipeline
pipe = AutoPipelineForText2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, variant="fp16").to("cuda")

# Initialize the image-to-image pipeline
image2image_pipe = AutoPipelineForImage2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, use_safetensors=True)
image2image_pipe.enable_model_cpu_offload()

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

model_index.json:   0%|          | 0.00/609 [00:00<?, ?B/s]

Fetching 19 files:   0%|          | 0/19 [00:00<?, ?it/s]

model.fp16.safetensors:   0%|          | 0.00/1.39G [00:00<?, ?B/s]

...

diffusion_pytorch_model.safetensors:   0%|          | 0.00/10.3G [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.78G [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/335M [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/335M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

In [ ]:
#from diffusers import AutoPipelineForText2Image
#import torch
#pipe = AutoPipelineForText2Image.from_pretrained("stabilityai/sdxl-turbo", torch_dtype=torch.float16, variant="fp16").to("cuda")

In [ ]:
#import torch
#from diffusers import AutoPipelineForImage2Image
#from diffusers.utils import load_image, make_image_grid

#pipe_i = AutoPipelineForImage2Image.from_pretrained(
#    "stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, use_safetensors=True
#)

#lora_safetensors_path = "/content/drive/MyDrive/kohya-trainer/output/1950s_drawing_style.safetensors"

#pipe.load_lora_weights(lora_safetensors_path)
#pipe_i.enable_model_cpu_offload()
# remove following line if xFormers is not installed or you have PyTorch 2.0 or higher installed
#pipeline.enable_xformers_memory_efficient_attention()

In [ ]:
%cd /content/

/content


In [ ]:
#@title Setup
!nvidia-smi
!git clone https://github.com/Stability-AI/generative-models.git
# install required packages from pypi
# !pip3 install -r generative-models/requirements/pt2.txt
# manually install only necesarry packages for colab
!wget https://gist.githubusercontent.com/mkshing/4ad40699756d996ba6b3f7934e6ca532/raw/3f0094272c7a2bd3eb5f1a0db91bed582c9e8f01/requirements.txt
#!pip3 uninstall -r requirements.txt -y
!pip3 install -r requirements.txt
!pip3 install -e generative-models
!pip3 install -e git+https://github.com/Stability-AI/datapipelines.git@main#egg=sdata
!pip3 install gradio

Sat Dec 30 22:59:44 2023       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA A100-SXM4-40GB          Off | 00000000:00:04.0 Off |                    0 |
| N/A   32C    P0              51W / 400W |   7379MiB / 40960MiB |      0%      Default |
|                                         |                      |             Disabled |
+-----------------------------------------+----------------------+--

Obtaining file:///content/generative-models
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Preparing editable metadata (pyproject.toml) ... done
  Building editable for sgm (pyproject.toml) ... done
  Created wheel for sgm: filename=sgm-0.1.0-py3-none-any.whl size=26919 sha256=59769caef6f4b1066bee086775bfd8ae2e532ee27c055ef03a3496379bcafff2
  Stored in directory: /tmp/pip-ephem-wheel-cache-jy4lt0ep/wheels/12/9b/27/03142f4dee9fa0a99f6c146eae81eb66e17b781145ecb05fa5
Successfully built sgm
Obtaining sdata from git+https://github.com/Stability-AI/datapipelines.git@main#egg=sdata
  Cloning https://github.com/Stability-AI/datapipelines.git (to revision main) to ./src/sdata
  Running command git clone --filter=blob:none --quiet https://github.com/Stability-AI/datapipelines.git /content/src/sdata
  Resolved https://github.com/Stability-AI/datapipelines.git to commit 8bce77d147033b3a5285b6

In [ ]:
%%writefile /content/loadmod.py
import sys
from omegaconf import OmegaConf
version = "svd_xt"
import torch

sys.path.append("generative-models")
from sgm.util import default, instantiate_from_config
from scripts.util.detection.nsfw_and_watermark_dectection import DeepFloydDataFiltering

def load_model(
    config: str,
    device: str,
    num_frames: int,
    num_steps: int,
):
    config = OmegaConf.load(config)
    config.model.params.conditioner_config.params.emb_models[
        0
    ].params.open_clip_embedding_config.params.init_device = device
    config.model.params.sampler_config.params.num_steps = num_steps
    config.model.params.sampler_config.params.guider_config.params.num_frames = (
        num_frames
    )
    with torch.device(device):
        model = instantiate_from_config(config.model).to(device).eval().requires_grad_(False)

    filter = DeepFloydDataFiltering(verbose=False, device=device)
    return model, filter


if version == "svd":
    num_frames = 14
    num_steps = 25
    # output_folder = default(output_folder, "outputs/simple_video_sample/svd/")
    model_config = "generative-models/scripts/sampling/configs/svd.yaml"
elif version == "svd_xt":
    num_frames = 25
    num_steps = 30
    # output_folder = default(output_folder, "outputs/simple_video_sample/svd_xt/")
    model_config = "generative-models/scripts/sampling/configs/svd_xt.yaml"
else:
    raise ValueError(f"Version {version} does not exist.")

device = "cuda" if torch.cuda.is_available() else "cpu"
model, filter = load_model(
    model_config,
    device,
    num_frames,
    num_steps,
)
# move models expect unet to cpu
model.conditioner.cpu()
model.first_stage_model.cpu()
# change the dtype of unet
model.model.to(dtype=torch.float16)
torch.cuda.empty_cache()
model = model.requires_grad_(False)

Writing /content/loadmod.py


In [ ]:
%cd /content/generative-models
#@title Colab hack for SVD
# !pip uninstall -y numpy
# !pip install -U numpy
!mkdir -p /content/scripts/util/detection
!ln -s /content/generative-models/scripts/util/detection/p_head_v1.npz /content/scripts/util/detection/p_head_v1.npz
!ln -s /content/generative-models/scripts/util/detection/w_head_v1.npz /content/scripts/util/detection/w_head_v1.npz

/content/generative-models


In [ ]:
%cd /content/generative-models

/content/generative-models


In [ ]:
# @title Download weights
import os
import subprocess
version = "svd_xt" #@param ["svd", "svd_xt"]
TYPE2PATH = {
    "svd": ["https://huggingface.co/stabilityai/stable-video-diffusion-img2vid/resolve/main/svd.safetensors", "checkpoints/svd.safetensors"],
    "svd_xt": ["https://huggingface.co/stabilityai/stable-video-diffusion-img2vid-xt/resolve/main/svd_xt.safetensors", "checkpoints/svd_xt.safetensors"]
}
download_from, download_to = TYPE2PATH[version]
# @markdown This will take several minutes. <br>
# @markdown **Reference:**
# @markdown * `svd`: [stabilityai/stable-video-diffusion-img2vid](https://huggingface.co/stabilityai/stable-video-diffusion-img2vid) for 14 frames generation
# @markdown * `svd_xt`: [stabilityai/stable-video-diffusion-img2vid-xt](https://huggingface.co/stabilityai/stable-video-diffusion-img2vid-xt) for 25 frames generation
os.makedirs("checkpoints", exist_ok=True)
if os.path.exists(download_to):
  print("Already downloaded")
else:
  print(f"download from {download_from} to {download_to}")
  subprocess.call(["wget", download_from, "-O", download_to])

download from https://huggingface.co/stabilityai/stable-video-diffusion-img2vid-xt/resolve/main/svd_xt.safetensors to checkpoints/svd_xt.safetensors


In [ ]:
!pip uninstall audiocraft -y

In [ ]:
%cd /content/generative-models
!python /content/loadmod.py
%cd /content

/content/generative-models
Traceback (most recent call last):
  File "/content/loadmod.py", line 45, in <module>
    model, filter = load_model(
  File "/content/loadmod.py", line 16, in load_model
    config = OmegaConf.load(config)
  File "/usr/local/lib/python3.10/dist-packages/omegaconf/omegaconf.py", line 189, in load
    with io.open(os.path.abspath(file_), "r", encoding="utf-8") as f:
FileNotFoundError: [Errno 2] No such file or directory: '/content/generative-models/generative-models/scripts/sampling/configs/svd_xt.yaml'
/content


In [ ]:
!pip install moviepy
%cd /content
!git clone -b dev https://github.com/camenduru/tortoise-hf
%cd /content/tortoise-hf
!git clone -b v1.0 https://github.com/camenduru/tortoise-tts

!pip install gradio scipy -U
%cd /content/tortoise-hf/tortoise-tts
!pip install transformers==4.19.0
!pip install -r requirements.txt
!python setup.py install

%cd /content/

/content
Cloning into 'tortoise-hf'...
remote: Enumerating objects: 117, done.
remote: Counting objects: 100% (117/117), done.
remote: Compressing objects: 100% (53/53), done.
remote: Total 117 (delta 64), reused 109 (delta 60), pack-reused 0
Receiving objects: 100% (117/117), 17.93 KiB | 17.93 MiB/s, done.
Resolving deltas: 100% (64/64), done.
/content/tortoise-hf
Cloning into 'tortoise-tts'...
remote: Enumerating objects: 1531, done.
remote: Total 1531 (delta 0), reused 0 (delta 0), pack-reused 1531
Receiving objects: 100% (1531/1531), 53.58 MiB | 15.39 MiB/s, done.
Resolving deltas: 100% (627/627), done.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.6/16.6 MB 83.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 305.1/305.1 kB 36.5 MB/s eta 0:00:00
  Attempting uninstall: gradio-client
    Found existing installation: gradio_client 0.7.0
    Uninstalling gradio_client-0.7.0:
      Successfully uninstalled gradio_client-0.7.0
  Attempting uninstall: gradio
    Found 

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.5/235.5 kB 11.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.4/34.4 MB 48.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.1/213.1 kB 28.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 88.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.0/8.0 MB 19.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 100.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.8/110.8 kB 16.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 819.1/819.1 kB 64.0 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of rotar

In [ ]:
#!pip3 install --pre torch torchvision torchaudio --index-url https://download.pytorch.org/whl/nightly/cu121
!pip install pyttsx3
!pip install sounddevice
!pip install soundfile
!sudo apt-get update
!sudo apt-get install aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/lj1995/VoiceConversionWebUI/resolve/main/hubert_base.pt -d /content/ -o hubert_base.pt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/lj1995/VoiceConversionWebUI/resolve/main/rmvpe.pt -d /content/ -o rmvpe.pt
!pip install -e git+https://github.com/JarodMica/rvc.git#egg=rvc
!pip install -e git+https://github.com/JarodMica/rvc-tts-pipeline.git#egg=rvc_tts_pipe
import sys
sys.path.append('/content/src/rvc')
sys.path.append('/content/src/rvc-tts-pipe')

Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Hit:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:3 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ Packages [48.6 kB]
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:5 http://security.ubuntu.com/ubuntu jammy-security InRelease [110 kB]
Get:6 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [119 kB]
Get:7 https://ppa.launchpadcontent.net/c2d4u.team/c2d4u4.0+/ubuntu jammy InRelease [18.1 kB]
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:10 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Get:11 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 Packages [1,599 kB]
Hit:12 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Get:13 http://security.ubuntu.com/ubuntu jammy-security/u

Obtaining rvc_tts_pipe from git+https://github.com/JarodMica/rvc-tts-pipeline.git#egg=rvc_tts_pipe
  Cloning https://github.com/JarodMica/rvc-tts-pipeline.git to ./src/rvc-tts-pipe
  Running command git clone --filter=blob:none --quiet https://github.com/JarodMica/rvc-tts-pipeline.git /content/src/rvc-tts-pipe
  Resolved https://github.com/JarodMica/rvc-tts-pipeline.git to commit e31ad03d43161a9edbe71fdb07e8ae96fd473de5
  Preparing metadata (setup.py) ... done
  Running setup.py develop for rvc_tts_pipe


In [ ]:
%%writefile /content/rvcscript.py
import sys
sys.path.append('/content/src/rvc')
sys.path.append('/content/src/rvc-tts-pipe')
from rvc_infer import rvc_convert
rvc_convert(model_path="/content/#voicervc/Narrator/DBZNarratorENG.pth", file_index="/content/#voicervc/Narrator/added_IVF992_Flat_nprobe_1_DBZNarratorENG_v2.index", f0_up_key=0, input_path="/content/out/daniel_0_0.wav")

Writing /content/rvcscript.py


In [ ]:
%%writefile DownTown.py
import os
import argparse
from yt_dlp import YoutubeDL
from moviepy.editor import VideoFileClip, concatenate_videoclips

# Create directories if they don't exist
if not os.path.exists('/content/vids'):
    os.makedirs('/content/vids')

if not os.path.exists('/content/#voicemp3'):
    os.makedirs('/content/#voicemp3')

# Function to download a video segment
def download_segment(start, end, index, video_url):
    ydl_opts = {
        'format': 'best',  # changed from '22' to 'best'
        'outtmpl': f'/content/vids/segment_{index}.mp4',
        'external_downloader': 'ffmpeg',
        'external_downloader_args': ['-ss', start, '-to', end]
    }

    with YoutubeDL(ydl_opts) as ydl:
        ydl.download([video_url])


# Command-line argument parsing
def main():
    parser = argparse.ArgumentParser(description="Download video segments, concatenate, and extract audio.")
    parser.add_argument("name", help="Name for the final video and audio files")
    parser.add_argument("video_url", help="URL of the YouTube video")
    parser.add_argument("timestamps", nargs="+", help="List of timestamps in the format 'start end'")
    parser.add_argument("-v", "--remove-video", action="store_true", help="Remove video file at the end")
    parser.add_argument("-a", "--remove-audio", action="store_true", help="Remove audio file at the end")
    parser.add_argument("-k", "--keep-both", action="store_true", help="Keep both audio and video files")

    args = parser.parse_args()
    name = args.name
    video_url = args.video_url
    timestamps = [tuple(timestamp.split()) for timestamp in args.timestamps]

    # Download each segment
    for i, (start_time, end_time) in enumerate(timestamps):
        download_segment(start_time, end_time, i, video_url)

    # Combine the segments
    segments = [VideoFileClip(f'/content/vids/segment_{i}.mp4') for i in range(len(timestamps))]
    final_clip = concatenate_videoclips(segments)
    final_clip.write_videofile(f"/content/vids/{name}.mp4")

    # Extract audio and save as MP3
    audio = final_clip.audio.set_fps(44100)
    audio.write_audiofile(f"/content/#voicemp3/{name}.mp3")

    # Clean up segment files
    for i in range(len(timestamps)):
        os.remove(f'/content/vids/segment_{i}.mp4')

    # Remove video and/or audio files if specified
    if args.remove_video and not args.keep_both:
        os.remove(f'/content/vids/{name}.mp4')
    if args.remove_audio and not args.keep_both:
        os.remove(f'/content/#voicemp3/{name}.mp3')

if __name__ == "__main__":
    main()


Writing DownTown.py


In [ ]:
%%writefile RVC-dl.py
import requests
import zipfile
import io
import os
import sys
import re
import gdown

def resolve_hugging_face_url(zip_url):
    response = requests.head(zip_url, allow_redirects=True)
    if response.status_code == 200:
        return response.url
    else:
        return None

def extract_google_drive(file_id, target_directory):
    temp_zip_path = "/content/temp_google_drive.zip"
    gdown.download(f"https://drive.google.com/uc?id={file_id}", temp_zip_path, quiet=False)

    with zipfile.ZipFile(temp_zip_path, 'r') as zip_ref:
        for file_info in zip_ref.infolist():
            if not file_info.is_dir():  # Only extract files
                file_info.filename = os.path.basename(file_info.filename)
                zip_ref.extract(file_info, target_directory)

    os.remove(temp_zip_path)
    print("ZIP file downloaded and extracted successfully from Google Drive.")

def extract_zip(zip_url, target_directory):
    os.makedirs(target_directory, exist_ok=True)

    if "drive.google.com" in zip_url:
        file_id_search = re.search(r"/file/d/([a-zA-Z0-9_-]+)/", zip_url)
        if file_id_search:
            file_id = file_id_search.group(1)
            extract_google_drive(file_id, target_directory)
        else:
            print("Invalid Google Drive URL.")
        return

    if "huggingface.co" in zip_url:
        zip_url = resolve_hugging_face_url(zip_url)
        if zip_url is None:
            print("Failed to resolve Hugging Face URL.")
            return

    response = requests.get(zip_url)
    if response.status_code == 200:
        with zipfile.ZipFile(io.BytesIO(response.content), 'r') as zip_ref:
            for file_info in zip_ref.infolist():
                if not file_info.is_dir():  # Only extract files
                    file_info.filename = os.path.basename(file_info.filename)
                    zip_ref.extract(file_info, target_directory)
        print("ZIP file downloaded and extracted successfully.")
    else:
        print("Failed to download ZIP file.")

if __name__ == "__main__":
    if len(sys.argv) != 3:
        print("Usage: python RVC-dl.py <target_directory> <zip_url>")
    else:
        target_directory = sys.argv[1]
        zip_url = sys.argv[2]
        extract_zip(zip_url, target_directory)


Writing RVC-dl.py


In [ ]:
!pip install gdown

In [ ]:
#!python RVC-dl.py "/content/#voicervc/Narrator/" "https://huggingface.co/SyberGen/DragonBallVModels/resolve/main/DBZNarratorENG.zip"
#!python RVC-dl.py "/content/#voicervc/cat10/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/cat10.zip"
#!python RVC-dl.py "/content/#voicervc/cat2/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/cat2.zip"
#!python RVC-dl.py "/content/#voicervc/dwight/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/dwight.zip"
#!python RVC-dl.py "/content/#voicervc/farts/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/farts.zip"
#!python RVC-dl.py "/content/#voicervc/farts2/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/farts2.zip"
#!python RVC-dl.py "/content/#voicervc/toby/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/toby.zip"
#!python RVC-dl.py "/content/#voicervc/tommycruiser/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/tommycruiser.zip"
#!python RVC-dl.py "/content/#voicervc/billclinton/" "https://huggingface.co/BibEBobberson/Presidents/resolve/main/Bill-Clinton-V2.zip"
#!python RVC-dl.py "/content/#voicervc/tomhanks/" "https://huggingface.co/Hell-Inspector/Hell-Inspectors-RVC-Archive/resolve/main/WoodyV2.zip"
#!python RVC-dl.py "/content/#voicervc/tomcruise/" "https://huggingface.co/spaces/DragonFarts/RVCmodels/resolve/main/tommycruiser.zip"
#!python RVC-dl.py "/content/#voicervc/tomdelonge/" "https://huggingface.co/SUP3RMASS1VE/TomDeLonge/resolve/main/TomDeLonge.zip"
#!python RVC-dl.py "/content/#voicervc/drewbarrymore/" "https://huggingface.co/iatop65/RVC_Voices/resolve/main/Jillian_Wilcox_Family_Guy.zip"
#!python RVC-dl.py "/content/#voicervc/Bart/" "https://huggingface.co/Biotin/BartSimpson/resolve/main/BartSimpson.zip"
#!python RVC-dl.py "/content/#voicervc/Homer/" "https://drive.google.com/file/d/1O6GOlcNJ8nBBppFXSZqdcBc3mOW3k4V8/view?usp=sharing"
#!python RVC-dl.py "/content/#voicervc/SamuelJackson/" "https://huggingface.co/ThompsonAI9/ThompsonAI9RVC/resolve/main/SamuelLJackson470v2.zip"
#!python RVC-dl.py "/content/#voicervc/Patton_Oswalt/" "https://huggingface.co/Dibe/Patton_Oswald/resolve/main/Patton_Oswalt.zip"
#!python RVC-dl.py "/content/#voicervc/Morgan_Freeman/" "https://drive.google.com/file/d/1jISYeUONMWbiir12g-r2E77xIdQ9atmp/view?usp=share_link"

In [ ]:
%%writefile /content/rvcscript.py
import sys
import argparse
sys.path.append('/content/src/rvc')
sys.path.append('/content/src/rvc-tts-pipe')
from rvc_infer import rvc_convert

# Create the parser
parser = argparse.ArgumentParser(description='Run RVC conversion with specified parameters.')

# Add arguments
parser.add_argument('--model_path', type=str, required=True, help='Path to the model file')
parser.add_argument('--file_index', type=str, required=True, help='Path to the file index')
parser.add_argument('--f0_up_key', type=int, default=0, help='F0 up key value (default: 0)')

# Parse the arguments
args = parser.parse_args()

# Run the rvc_convert function with the provided arguments
rvc_convert(model_path=args.model_path, file_index=args.file_index, f0_up_key=args.f0_up_key, input_path="/content/out/daniel_0_0.wav")


Overwriting /content/rvcscript.py


In [ ]:
#%cd /content/
#!python /content/rvcscript.py --model_path "/content/drive/MyDrive/#BACKUPS/#voicervc/Homer/HomerV2_600.pth" --file_index "/content/drive/MyDrive/#BACKUPS/#voicervc/Homer/added_IVF2143_Flat_nprobe_1_v2.index" --f0_up_key 1
#%cd /content/

In [ ]:
!python3 -m pip install -U git+https://github.com/facebookresearch/demucs#egg=demucs


  Cloning https://github.com/facebookresearch/demucs to /tmp/pip-install-map5zxh5/demucs_1db8116f02a04e6eba3f21f2d7379d2d
  Running command git clone --filter=blob:none --quiet https://github.com/facebookresearch/demucs /tmp/pip-install-map5zxh5/demucs_1db8116f02a04e6eba3f21f2d7379d2d
  Resolved https://github.com/facebookresearch/demucs to commit e976d93ecc3865e5757426930257e200846a520a
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 87.1/87.1 kB 2.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.6/59.6 kB 6.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 239.8/239.8 kB 16.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.7/46.7 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 74.7/74.7 kB 10.9 MB/s 

In [ ]:
!pip install pytube

In [ ]:
%%writefile /content/pytube_inf.py
import os
import pytube
import subprocess
import argparse

def download_video(youtube_link, output_file_path, format):
    try:
        yt = pytube.YouTube(youtube_link)

        # Ensure the directory exists
        output_directory = os.path.dirname(output_file_path)
        if not os.path.exists(output_directory):
            os.makedirs(output_directory)

        if format == "mp3":
            stream = yt.streams.filter(only_audio=True).first()
            if not stream:
                raise ValueError("No audio stream found")

            # Download the video
            temp_video_path = stream.download(output_directory)

            # Convert to MP3
            subprocess.run(["ffmpeg", "-i", temp_video_path, output_file_path])
            os.remove(temp_video_path)  # Delete the original video file
            print("Audio converted and saved as MP3 successfully!")
        else:
            raise ValueError("This script currently only supports MP3 format")

    except Exception as e:
        print(f"An error occurred: {e}")

if __name__ == "__main__":
    parser = argparse.ArgumentParser(description='Download YouTube videos as MP3.')
    parser.add_argument('youtube_link', type=str, help='YouTube video link')
    parser.add_argument('output_file_path', type=str, help='Full path for the output MP3 file')
    parser.add_argument('format', type=str, choices=['mp3'], help='Download format (currently only supports mp3)')

    args = parser.parse_args()

    download_video(args.youtube_link, args.output_file_path, args.format)


Overwriting /content/pytube_inf.py


In [ ]:
%%writefile /content/mp3split.py
from pydub import AudioSegment
import os

def split_mp3_to_mono_wav(source_folder, target_folder, segment_length=60 * 1000):  # 60 * 1000 ms = 1 minute
    if not os.path.exists(target_folder):
        os.makedirs(target_folder)

    for filename in os.listdir(source_folder):
        if filename.endswith(".mp3"):
            path = os.path.join(source_folder, filename)
            audio = AudioSegment.from_mp3(path)

            # Calculate the number of segments
            length_audio = len(audio)
            total_segments = length_audio // segment_length + (1 if length_audio % segment_length else 0)

            for i in range(total_segments):
                start_time = i * segment_length
                end_time = min(start_time + segment_length, length_audio)

                split_audio = audio[start_time:end_time]
                # Convert to mono
                split_audio = split_audio.set_channels(1)
                split_filename = f"{os.path.splitext(filename)[0]}_{i}.wav"
                split_audio.export(os.path.join(target_folder, split_filename), format="wav")

# Replace '/content/seperate_out/htdemucs/audio' with the path to your source mp3 files
# Replace '/content/seperate_out/htdemucs/audio/split' with the path where you want to save the split files
source_folder = '/content/seperate_out/htdemucs/audio'
target_folder = '/content/seperate_out/htdemucs/audio/split'

split_mp3_to_mono_wav(source_folder, target_folder)


Writing /content/mp3split.py


In [ ]:
%%writefile /content/demuc.py
# Customize the following options!
model = "htdemucs"
extensions = ["mp3", "wav", "ogg", "flac"]  # we will look for all those file types.
two_stems = None   # only separate one stems from the rest, for instance
# two_stems = "vocals"

# Options for the output audio.
mp3 = True
mp3_rate = 320
float32 = False  # output as float 32 wavs, unsused if 'mp3' is True.
int24 = False    # output as int24 wavs, unused if 'mp3' is True.
# You cannot set both `float32 = True` and `int24 = True` !!

in_path = '/content/youtube_out/'
out_path = '/content/seperate_out/'
import io
from pathlib import Path
import select
from shutil import rmtree
import subprocess as sp
import sys
from typing import Dict, Tuple, Optional, IO

from google.colab import files

def find_files(in_path):
    out = []
    for file in Path(in_path).iterdir():
        if file.suffix.lower().lstrip(".") in extensions:
            out.append(file)
    return out

def copy_process_streams(process: sp.Popen):
    def raw(stream: Optional[IO[bytes]]) -> IO[bytes]:
        assert stream is not None
        if isinstance(stream, io.BufferedIOBase):
            stream = stream.raw
        return stream

    p_stdout, p_stderr = raw(process.stdout), raw(process.stderr)
    stream_by_fd: Dict[int, Tuple[IO[bytes], io.StringIO, IO[str]]] = {
        p_stdout.fileno(): (p_stdout, sys.stdout),
        p_stderr.fileno(): (p_stderr, sys.stderr),
    }
    fds = list(stream_by_fd.keys())

    while fds:
        # `select` syscall will wait until one of the file descriptors has content.
        ready, _, _ = select.select(fds, [], [])
        for fd in ready:
            p_stream, std = stream_by_fd[fd]
            raw_buf = p_stream.read(2 ** 16)
            if not raw_buf:
                fds.remove(fd)
                continue
            buf = raw_buf.decode()
            std.write(buf)
            std.flush()

def separate(inp=None, outp=None):
    inp = inp or in_path
    outp = outp or out_path
    cmd = ["python3", "-m", "demucs.separate", "-o", str(outp), "-n", model]
    if mp3:
        cmd += ["--mp3", f"--mp3-bitrate={mp3_rate}"]
    if float32:
        cmd += ["--float32"]
    if int24:
        cmd += ["--int24"]
    if two_stems is not None:
        cmd += [f"--two-stems={two_stems}"]
    files = [str(f) for f in find_files(inp)]
    if not files:
        print(f"No valid audio files in {in_path}")
        return
    print("Going to separate the files:")
    print('\n'.join(files))
    print("With command: ", " ".join(cmd))
    p = sp.Popen(cmd + files, stdout=sp.PIPE, stderr=sp.PIPE)
    copy_process_streams(p)
    p.wait()
    if p.returncode != 0:
        print("Command failed, something went wrong.")


def from_upload():
    out_path = Path('separated')
    in_path = Path('tmp_in')

    if in_path.exists():
        rmtree(in_path)
    in_path.mkdir()

    if out_path.exists():
        rmtree(out_path)
    out_path.mkdir()

    uploaded = files.upload()
    for name, content in uploaded.items():
        (in_path / name).write_bytes(content)
    separate(in_path, out_path)

separate()

Writing /content/demuc.py


In [ ]:
#!pip install -q torch==1.13.1+cu116 torchvision==0.14.1+cu116 torchaudio==0.13.1 torchtext==0.14.1 torchdata==0.5.1 --extra-index-url https://download.pytorch.org/whl/cu116 -U
!git clone https://huggingface.co/camenduru/Wav2Lip
#!pip install gradio yt_dlp ffmpeg-python librosa==0.8.0
%cd /content/Wav2Lip

Cloning into 'Wav2Lip'...
remote: Enumerating objects: 72, done.
remote: Counting objects: 100% (3/3), done.
remote: Compressing objects: 100% (3/3), done.
remote: Total 72 (delta 0), reused 0 (delta 0), pack-reused 69
Unpacking objects: 100% (72/72), 442.42 KiB | 1.03 MiB/s, done.
Filtering content: 100% (6/6), 936.88 MiB | 205.21 MiB/s, done.
/content/Wav2Lip


In [ ]:
%%writefile /content/music1.py
import argparse
from audiocraft.models import MusicGen, MultiBandDiffusion
import soundfile as sf
from audiocraft.utils.notebook import display_audio

# Initialize the MusicGen model
USE_DIFFUSION_DECODER = False
model = MusicGen.get_pretrained('facebook/musicgen-large')
if USE_DIFFUSION_DECODER:
    mbd = MultiBandDiffusion.get_mbd_musicgen()

# Function to generate music
def generate_music(description, duration, output_name):
    # Set generation parameters
    model.set_generation_params(
        use_sampling=True,
        top_k=250,
        duration=duration
    )

    # Generate music
    output = model.generate(
        descriptions=[description],
        progress=True, return_tokens=True
    )

    # Process and save the audio
    audio_data_cpu = output[0].cpu().numpy().reshape(-1)
    sf.write(output_name, audio_data_cpu, 32000)

    # Display the audio (comment this out if running in a non-interactive environment)
    # display_audio(output[0], sample_rate=32000)

    # Additional code for diffusion decoder, if used
    if USE_DIFFUSION_DECODER:
        out_diffusion = mbd.tokens_to_wav(output[1])
        # display_audio(out_diffusion, sample_rate=32000)  # Comment out if non-interactive
        out_diffusion_cpu = out_diffusion.cpu().numpy().reshape(-1)
        sf.write(output_name.replace('.wav', '_Diffusion.wav'), out_diffusion_cpu, 32000)

# Set up argument parser
parser = argparse.ArgumentParser(description="Generate music based on provided description.")
parser.add_argument('--description', type=str, required=True, help='Description of the music to generate.')
parser.add_argument('--duration', type=int, default=30, help='Duration of the music in seconds.')
parser.add_argument('--output_name', type=str, default='/content/Audio_Out.wav', help='Output WAV file name.')

# Parse arguments
args = parser.parse_args()

# Generate music with provided arguments
generate_music(args.description, args.duration, args.output_name)


Writing /content/music1.py


In [ ]:
!mkdir /content/youtube_out
!mkdir /content/seperate_out


mkdir: cannot create directory ‘/content/youtube_out’: File exists


In [ ]:
!pip uninstall xformers transformers -y
!pip install xformers transformers

Found existing installation: xformers 0.0.22
Uninstalling xformers-0.0.22:
  Successfully uninstalled xformers-0.0.22
Found existing installation: transformers 4.19.0
Uninstalling transformers-4.19.0:
  Successfully uninstalled transformers-4.19.0
  Using cached xformers-0.0.23.post1-cp310-cp310-manylinux2014_x86_64.whl (213.0 MB)
  Using cached transformers-4.36.2-py3-none-any.whl (8.2 MB)
  Using cached tokenizers-0.15.0-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.8 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.12.1
    Uninstalling tokenizers-0.12.1:
      Successfully uninstalled tokenizers-0.12.1


# Setup Goosey-GUI

## sign up at ngrok for free account and put api key here

In [ ]:
!ngrok config add-authtoken YOUR_API_KEY_HERE

Authtoken saved to configuration file: /root/.config/ngrok/ngrok.yml


In [ ]:
!mkdir /content/gooseygui

## add your LoRas to the list i have this just as example

In [ ]:
%%writefile /content/gooseygui/loralist.txt
{
    "Pyrotechnics": "/content/drive/MyDrive/kohya-trainer/output/Pyrotechnics.safetensors",
    "Blotterart": "/content/drive/MyDrive/kohya-trainer/output/BlotterArt.safetensors",
}


Writing /content/gooseygui/loralist.txt


## Easily EDITABLE GOOSE-GUI  HTML Front_END

In [ ]:
%%writefile /content/gooseygui/gooseygui.html

<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>Image Generator</title>
    <style>
        .container {
            width: 80%;
            margin: auto;
            text-align: center;
            display: flex;
            flex-direction: column;
            align-items: center;
        }
        #imageForm, #imageModForm, #imageUploadForm, #modelSelectForm {
            margin-bottom: 20px;
        }
        #canvasContainer {
            display: flex;
            flex-direction: row;
        }
        #imageList {
            list-style: none;
            padding: 0;
            margin: 0;
            overflow-y: auto;
            max-height: 200px;
        }
        #objectCanvas {
            border: 2px solid black;
            cursor: crosshair;
        }
        #objectSize {
            margin-top: 10px;
        }
#videoList {
    list-style: none;
    padding: 0;
    margin: 0;
    overflow-y: auto;
    max-height: 400px; /* Adjust height to match video player */
    width: 200px; /* Adjust width as needed */
}

#videoList video {
    width: 100%; /* Make videos fill the width of the list */
    margin-bottom: 10px; /* Space between videos */
    border: 1px solid #ddd;
}

    </style>
</head>
<body>

    <div>
        <label for="growOverTime">Enable Grow Over Time:</label>
        <input type="checkbox" id="growOverTime" name="growOverTime">
    </div>
    <div>
        <label for="startWidth">Start Width:</label>
        <input type="number" id="startWidth" name="startWidth" value="50">
    </div>
    <div>
        <label for="startHeight">Start Height:</label>
        <input type="number" id="startHeight" name="startHeight" value="50">
    </div>
    <div>
        <label for="growOverTimeAmount">Grow Amount:</label>
        <input type="number" id="growOverTimeAmount" name="growOverTimeAmount" value="5">
    </div>
<div>
    <label for="rotateOvertime">Enable Rotate Over Time:</label>
    <input type="checkbox" id="rotateOvertime" name="rotateOvertime">
</div>
<div>
    <label for="startRotation">Start Rotation (degrees):</label>
    <input type="number" id="startRotation" name="startRotation" value="0">
</div>
<div>
    <label for="rotateOverTimeAmount">Rotate Amount Over Time (degrees):</label>
    <input type="number" id="rotateOverTimeAmount" name="rotateOverTimeAmount" value="1">
</div>

    <div>
        <label for="autoPlaceMs">Auto-Place Interval (ms):</label>
        <input type="number" id="autoPlaceMs" name="autoPlaceMs" value="100">
    </div>
    <div>
        <label for="autoPlace">Enable Auto-Place:</label>
        <input type="checkbox" id="autoPlace" name="autoPlace">
    </div>

    <form id="canvasSizeForm">
        <div>
            <label for="canvasWidth">Canvas Width:</label>
            <input type="number" id="canvasWidth" name="canvasWidth" value="400">
        </div>
        <div>
            <label for="canvasHeight">Canvas Height:</label>
            <input type="number" id="canvasHeight" name="canvasHeight" value="400">
        </div>
        <div>
            <button type="button" id="setCanvasSize">Set Canvas Size</button>
        </div>
    </form>
    <div class="container">
        <h1>Image Generator</h1>
        <form id="imageForm">
            <div>
                <label for="prompt">Enter Prompt:</label>
                <input type="text" id="prompt" name="prompt">
            </div>
            <div>
                <label for="removebg">Remove Background:</label>
                <input type="checkbox" id="removebg" name="removebg">
            </div>
            <div>
                <label for="width">Width:</label>
                <input type="number" id="width" name="width" value="512">
            </div>
            <div>
                <label for="height">Height:</label>
                <input type="number" id="height" name="height" value="512">
            </div>
            <div>
                <button type="submit">Generate Image</button>
            </div>
        </form>
        <form id="imageModForm">
            <div>
                <label for="modifyPrompt">Modify Image Prompt:</label>
                <input type="text" id="modifyPrompt" name="modifyPrompt">
            </div>
            <div>
                <label for="strength">Strength:</label>
                <input type="number" id="strength" name="strength" step="0.01" min="0" max="1" value="0.27">
            </div>
            <div>
                <label for="modRemovebg">Remove Background:</label>
                <input type="checkbox" id="modRemovebg" name="modRemovebg">
            </div>
            <div>
                <button type="button" id="modifyImage">Modify Image</button>
            </div>
        </form>
        <form id="imageUploadForm">
            <div>
                <label for="imageUpload">Upload Image:</label>
                <input type="file" id="imageUpload" name="imageUpload" accept="image/*">
            </div>
            <button type="button" id="uploadImage">Add to List</button>
        </form>
        <div id="canvasContainer">
            <canvas id="imageCanvas" width="400" height="400"></canvas>
            <ul id="imageList"></ul>
            <canvas id="objectCanvas" width="400" height="400"></canvas>
        </div>
        <div id="objectSize">
            <label for="objectWidth">Object Width:</label>
            <input type="number" id="objectWidth" name="objectWidth" step="1" min="1">
            <label for="objectHeight">Object Height:</label>
            <input type="number" id="objectHeight" name="objectHeight" step="1" min="1">
            <label for="objectRotation">Object Rotation (degrees):</label>
            <input type="number" id="objectRotation" name="objectRotation" step="1" min="0" max="360">
            <button id="saveDraw">Save Draw</button>
            <button id="clearCanvas">Clear Canvas</button>
        </div>
        <form id="pipelineChangeForm">
            <div>
                <label for="modelName">Model Name:</label>
                <input type="text" id="modelName" name="modelName" placeholder="e.g., stabilityai/sdxl-turbo">
            </div>
            <div>
                <label for="pipelineType">Select Pipeline Type:</label>
                <select id="pipelineType" name="pipelineType">
                    <option value="TXT">Text-to-Image</option>
                    <option value="IMG">Image-to-Image</option>
                </select>
            </div>
            <div>
                <button type="button" id="changePipeline">Change Pipeline</button>
            </div>
        </form>
        <form id="modelSelectForm">
            <div>
                <label for="loraPathsDropdown">LoRA Path:</label>
                <select id="loraPathsDropdown"></select>
            </div>
            <div>
                <label for="loraPath">LoRA File Path:</label>
                <input type="text" id="loraPath" name="loraPath">
            </div>
            <div>
                <label for="loraScale">LoRA Scale:</label>
                <input type="number" id="loraScale" name="loraScale" step="0.1" min="0" value="1">
            </div>
            <div>
                <label for="modelType">Select Model Type:</label>
                <select id="modelType" name="modelType">
                    <option value="TXT">Text-to-Image</option>
                    <option value="IMG">Image-to-Image</option>
                </select>
            </div>
            <div>
                <button type="button" id="selectModel">Select Model</button>
            </div>
        </form>
    </div>

<div id="mediaContainer" style="display: flex;">
    <div id="videoContainer" style="border:2px solid green; margin-right: 20px;">
        <video id="videoPlayer" width="400" height="400" controls></video>
    </div>
    <ul id="videoList"></ul>
</div>
<div>
    <label for="videoUpload">Upload MP4 Video:</label>
    <input type="file" id="videoUpload" name="videoUpload" accept="video/mp4">
    <button type="button" id="uploadVideoBtn">Upload</button>
</div>
<button id="makeVideo">Make Video</button>
    <div>
        <label for="fpsId">FPS ID:</label>
        <input type="number" id="fpsId" name="fpsId" value="30">
    </div>
    <div>
        <label for="numFrames">Number of Frames:</label>
        <input type="number" id="numFrames" name="numFrames" value="25">
    </div>
    <div>
        <label for="numSteps">Number of Steps:</label>
        <input type="number" id="numSteps" name="numSteps" value="30">
    </div>
    <div>
        <label for="seed">Seed:</label>
        <input type="number" id="seed" name="seed" value="23">
    </div>
    <div>
        <label for="decodingT">Decoding T:</label>
        <input type="number" id="decodingT" name="decodingT" value="5">
    </div>
    <div>
        <label for="motionBucketId">Motion Bucket ID:</label>
        <input type="number" id="motionBucketId" name="motionBucketId" value="100">
    </div>
    <div>

</div>

    <!-- TTS Section -->
    <div class="container">
        <h1>Text-to-Speech Generator</h1>
        <form id="ttsForm">
            <div>
                <label for="ttsModelPath">Model Path:</label>
                <input type="text" id="ttsModelPath" name="ttsModelPath">
            </div>
            <div>
                <label for="ttsFileIndex">File Index:</label>
                <input type="text" id="ttsFileIndex" name="ttsFileIndex">
            </div>
            <div>
                <label for="ttsF0UpKey">F0 Up Key:</label>
                <input type="number" id="ttsF0UpKey" name="ttsF0UpKey">
            </div>
            <div>
                <label for="ttsText">Text:</label>
                <input type="text" id="ttsText" name="ttsText">
            </div>
            <div>
                <label for="ttsVoice">Voice:</label>
                <input type="text" id="ttsVoice" name="ttsVoice">
            </div>
            <div>
                <label for="ifRVC">Use RVC:</label>
                <input type="checkbox" id="ifRVC" name="ifRVC">
            </div>
            <div>
                <button type="button" id="generateTTS">Generate TTS</button>
            </div>
            <div>
                <label for="uploadWav">Upload WAV File:</label>
                <input type="file" id="uploadWav" name="uploadWav" accept=".wav">
                <button type="button" id="uploadWavBtn">Upload</button>
            </div>
            <button type="button" id="rvcConvertBtn">RVC Convert</button>
<div class="container">
    <h1>YouTube Audio Extractor</h1>
    <form id="tubeForm">
        <div>
            <label for="youtubeLink">YouTube Link:</label>
            <input type="text" id="youtubeLink" name="youtubeLink">
        </div>
        <div>
            <button type="button" id="makeTube">Extract Audio</button>
        </div>

    </form>
</div>
    <div>
        <button id="addToSendList">Add to Send List</button>
        <button id="clearSendList">Clear List</button>
        <button id="makeAudio">Make Audio</button>
        <button id="appendAudio">Append Audio</button>


    </div>
    <ul id="sendList" style="margin-top: 20px;"></ul> <!-- Add this list for the send list -->

            <div class="container">

                <ul id="wavList"></ul>

                <button id="playWav" disabled>Play</button>
                <button id="downloadWav" disabled>Download</button>
                <audio id="audioPlayer" controls style="display: none;"></audio>
            </div>

        </form>
        <ul id="ttsList"></ul>
<select id="rvcConfigDropdown"></select>


<select id="otherNamesDropdown"></select>


    </div>
<div class="container">
    <h1>Wav2Lip Video Generator</h1>
    <div>
        <label for="inputTypeSelect">Select Input Type:</label>
        <select id="inputTypeSelect">
            <option value="image">Image</option>
            <option value="video">Video</option>
        </select>
    </div>
    <div>
        <button type="button" id="generateWav2LipVideo">Generate Wav2Lip Video</button>
    </div>
    <div class="container">
    <h1>Music Generator</h1>
    <form id="songForm">
        <div>
            <label for="songDuration">Duration (seconds):</label>
            <input type="number" id="songDuration" name="songDuration" value="30">
        </div>
        <div>
            <label for="songPrompt">Music Description:</label>
            <input type="text" id="songPrompt" name="songPrompt">
        </div>
        <div>
            <button type="button" id="generateSong">Generate Song</button>
        </div>
    </form>
    <ul id="songList"></ul> <!-- Add this line for the song list -->

    <div>
        <audio id="songPlayer" controls style="display: none;"></audio>
        <button id="downloadSong" disabled>Download</button>
    </div>
</div>
</div>

<script>
    const canvas = document.getElementById('imageCanvas');
    const objectCanvas = document.getElementById('objectCanvas');
    const ctx = canvas.getContext('2d');
    const objectCtx = objectCanvas.getContext('2d');
    const imageList = document.getElementById('imageList');
    const objectWidthInput = document.getElementById('objectWidth');
    const objectHeightInput = document.getElementById('objectHeight');
    const objectRotationInput = document.getElementById('objectRotation');
    const saveDrawButton = document.getElementById('saveDraw');
    const clearCanvasButton = document.getElementById('clearCanvas');
    const growOverTimeCheckbox = document.getElementById('growOverTime');
    const startWidthInput = document.getElementById('startWidth');
    const startHeightInput = document.getElementById('startHeight');
    const growOverTimeAmountInput = document.getElementById('growOverTimeAmount');
    const rotateOvertimeCheckbox = document.getElementById('rotateOvertime');
    const startRotationInput = document.getElementById('startRotation');
    const rotateOverTimeAmountInput = document.getElementById('rotateOverTimeAmount');
    let autoDrawInterval;
    let isDrawing = false;
    let lastMouseX = null;
    let lastMouseY = null;
    let currentWidth = parseInt(startWidthInput.value);
    let currentHeight = parseInt(startHeightInput.value);
    let currentRotation = parseInt(startRotationInput.value);
    const autoPlaceMsInput = document.getElementById('autoPlaceMs');
    const autoPlaceCheckbox = document.getElementById('autoPlace');
    let songs = {};
    let sendList = []; // To store the list of selected WAV files to send

document.getElementById('appendAudio').addEventListener('click', function() {
    if (sendList.length > 0) {
        var formData = new FormData();
        sendList.forEach(key => {
            if (ttsBlobs[key]) {
                formData.append('audio_files', ttsBlobs[key], key);
            }
        });

        fetch('/append_audio', {
            method: 'POST',
            body: formData
        })
        .then(response => response.blob())
        .then(blob => {
            var newAudioKey = 'AppendedAudio_' + Date.now();
            ttsBlobs[newAudioKey] = blob;
            addWavToList(newAudioKey);
        })
        .catch(error => console.error('Error:', error));
    } else {
        alert('Please add WAV files to the send list.');
    }
});











// Event listener for 'Add to Send List' button
document.getElementById('addToSendList').addEventListener('click', function() {
    if (currentSelectedWavKey) {
        sendList.push(currentSelectedWavKey);
        updateSendListUI();
    }
});

// Event listener for 'Clear List' button
document.getElementById('clearSendList').addEventListener('click', function() {
    sendList = [];
    updateSendListUI();
});

// Function to update the send list UI
function updateSendListUI() {
    const sendListElement = document.getElementById('sendList');
    sendListElement.innerHTML = ''; // Clear current list

    sendList.forEach(key => {
        const listItem = document.createElement('li');
        listItem.textContent = key;
        sendListElement.appendChild(listItem);
    });
}

document.getElementById('makeAudio').addEventListener('click', function() {
    if (sendList.length > 0) {
        var formData = new FormData();
        sendList.forEach(key => {
            if (ttsBlobs[key]) {
                formData.append('audio_files', ttsBlobs[key], key);
            }
        });

        fetch('/make_audio', {
            method: 'POST',
            body: formData
        })
        .then(response => response.blob())
        .then(blob => {
            var newAudioKey = 'CombinedAudio_' + Date.now();
            ttsBlobs[newAudioKey] = blob;
            addWavToList(newAudioKey);
        })
        .catch(error => console.error('Error:', error));
    } else {
        alert('Please add WAV files to the send list.');
    }
});


function addYoutubeAudioToList(filename, fileUrl) {
    var listItem = document.createElement('li');
    listItem.textContent = filename;
    listItem.dataset.textKey = filename;
    listItem.dataset.audioUrl = fileUrl;

    listItem.addEventListener('click', function() {
        // Mark as selected
        document.querySelectorAll('#wavList li').forEach(li => li.classList.remove('selected'));
        listItem.classList.add('selected');

        // Enable play and download buttons
        document.getElementById('playWav').disabled = false;
        document.getElementById('downloadWav').disabled = false;

        // Set global currentSelectedWavKey
        currentSelectedWavKey = filename;

        // Update audio player for playback
        var audioPlayer = document.getElementById('audioPlayer');
        audioPlayer.src = fileUrl;
        audioPlayer.style.display = 'block';
    });

    document.getElementById('wavList').appendChild(listItem);
}

document.getElementById('uploadVideoBtn').addEventListener('click', function() {
    var videoUploadInput = document.getElementById('videoUpload');
    if (videoUploadInput.files && videoUploadInput.files[0]) {
        var file = videoUploadInput.files[0];
        if (file.type !== 'video/mp4') {
            alert('Please upload an MP4 video.');
            return;
        }

        var url = URL.createObjectURL(file);
        addToVideoList(url);
    }
});

function addToVideoList(videoUrl) {
    const video = document.createElement('video');
    video.src = videoUrl;
    video.controls = true;
    video.width = 200; // Adjust width as needed

    const listItem = document.createElement('li');
    listItem.appendChild(video);
    document.getElementById('videoList').appendChild(listItem);
}




document.getElementById('rvcConvertBtn').addEventListener('click', function() {
    if (!currentSelectedWavKey || !ttsBlobs[currentSelectedWavKey]) {
        alert('Please select a WAV file from the list');
        return;
    }

    var formData = new FormData();
    formData.append('file', ttsBlobs[currentSelectedWavKey]);

    // Extract additional parameters if needed
    var modelPath = document.getElementById('ttsModelPath').value;
    var fileIndex = document.getElementById('ttsFileIndex').value;
    var f0UpKey = document.getElementById('ttsF0UpKey').value;

    formData.append('model_path', modelPath);
    formData.append('file_index', fileIndex);
    formData.append('f0_up_key', f0UpKey);

    fetch('/rvc_convert', {
        method: 'POST',
        body: formData
    })
    .then(response => response.blob())
    .then(blob => {
        var newFileName = 'RVC-' + currentSelectedWavKey;
        ttsBlobs[newFileName] = blob;
        addWavToList(newFileName);
    })
    .catch(error => console.error('Error:', error));
});


document.getElementById('uploadWavBtn').addEventListener('click', function() {
    var uploadInput = document.getElementById('uploadWav');
    if (uploadInput.files && uploadInput.files[0]) {
        var file = uploadInput.files[0];
        if (file.type !== 'audio/wav') {
            alert('Please upload a WAV file.');
            return;
        }

        var reader = new FileReader();
        reader.onload = function(e) {
            var blob = new Blob([e.target.result], {type: 'audio/wav'});
            var filename = file.name;

            ttsBlobs[filename] = blob;
            addWavToList(filename);
        };
        reader.readAsArrayBuffer(file);
    }
});







    // Event listener for the song generation button
    document.getElementById('generateSong').addEventListener('click', function() {
        var duration = document.getElementById('songDuration').value;
        var prompt = document.getElementById('songPrompt').value;

        fetch('/make_song', {
            method: 'POST',
            body: JSON.stringify({ duration: duration, prompt: prompt }),
            headers: {
                'Content-Type': 'application/json'
            }
        })
        .then(response => response.blob())
        // After generating song, add it to the song list
        .then(blob => {
            var url = URL.createObjectURL(blob);
            var duration = document.getElementById('songDuration').value;
            var prompt = document.getElementById('songPrompt').value;
            var songKey = duration + 's - ' + prompt; // Create a unique key for the song
            songs[songKey] = url; // Store the song URL with the key

            // Add the song to the song list
            var songList = document.getElementById('songList');
            var listItem = document.createElement('li');
            listItem.textContent = songKey;
            listItem.dataset.songKey = songKey;
            listItem.addEventListener('click', function() {
                // Deselect all other items
                document.querySelectorAll('#songList li').forEach(li => {
                    li.classList.remove('selected');
                    li.textContent = li.dataset.songKey;
                });

                // Select this item
                this.classList.add('selected');
                this.textContent = '→ ' + songKey;

                // Update the audio player and enable download button
                var songPlayer = document.getElementById('songPlayer');
                songPlayer.src = songs[songKey];
                songPlayer.style.display = 'block';

                var downloadBtn = document.getElementById('downloadSong');
                downloadBtn.disabled = false;
                downloadBtn.onclick = function() {
                    var a = document.createElement('a');
                    a.href = songs[songKey];
                    a.download = songKey + '.wav';
                    document.body.appendChild(a);
                    a.click();
                    document.body.removeChild(a);
                };
            });
            songList.appendChild(listItem);
        })
        .catch(error => console.error('Error:', error));
    });




document.getElementById('generateWav2LipVideo').addEventListener('click', function() {
    // First, determine if we're using an image or video
    const inputType = document.getElementById('inputTypeSelect').value;
    let selectedMediaBlob = null;

    if (inputType === 'image') {
        // If an image is selected, use it
        const selectedImage = document.querySelector('#imageList li.selected img');
        if (!selectedImage) {
            alert('Please select an image from the list');
            return;
        }
        // Fetch the image blob from the selected image source
        fetch(selectedImage.src)
            .then(response => response.blob())
            .then(blob => {
                selectedMediaBlob = blob;
                processWav2Lip(selectedMediaBlob);
            });
    } else {
        // If a video is to be used, get it from the video player
        const videoPlayer = document.getElementById('videoPlayer');
        const selectedVideoSrc = videoPlayer.src;
        if (!selectedVideoSrc) {
            alert('Please load a video in the player.');
            return;
        }
        // Fetch the video blob from the video player source
        fetch(selectedVideoSrc)
            .then(response => response.blob())
            .then(blob => {
                selectedMediaBlob = blob;
                processWav2Lip(selectedMediaBlob);
            });
    }
});

function processWav2Lip(mediaBlob) {
    if (!currentSelectedWavKey || !ttsBlobs[currentSelectedWavKey]) {
        alert('Please select a TTS audio from the list');
        return;
    }
    const selectedAudioBlob = ttsBlobs[currentSelectedWavKey];

    var formData = new FormData();
    formData.append('inputMedia', mediaBlob); // Updated key to 'inputMedia'
    formData.append('inputAudio', selectedAudioBlob); // Key for audio remains the same

    fetch('/wav2lip', {
        method: 'POST',
        body: formData
    })
    .then(response => {
        if (!response.ok) {
            throw new Error(`HTTP error! status: ${response.status}`);
        }
        return response.blob();
    })
    .then(blob => {
        var url = URL.createObjectURL(blob);
        addToVideoList(url);
    })
    .catch(error => {
        console.error('Error:', error);
        alert('Error processing Wav2Lip video. Please try again.');
    });
}








document.addEventListener('DOMContentLoaded', function() {
    // Fetch RVC configurations and populate the dropdown
    fetch('/get_rvc_configurations')
        .then(response => response.json())
        .then(configurations => {
            const rvcConfigDropdown = document.getElementById('rvcConfigDropdown');
            configurations.forEach((config, index) => {
                const option = document.createElement('option');
                option.value = index; // Index of the configuration in the array
                option.textContent = config[0]; // Use the first element as the name
                rvcConfigDropdown.appendChild(option);
            });

            // Event listener for RVC configuration dropdown
            rvcConfigDropdown.addEventListener('change', function() {
                const selectedConfig = configurations[this.value];
                document.getElementById('ttsModelPath').value = selectedConfig[2]; // model_path
                document.getElementById('ttsFileIndex').value = selectedConfig[1]; // file_index
                document.getElementById('ttsF0UpKey').value = selectedConfig[3]; // f0_up_key
            });
        });

    // Fetch other names and populate the dropdown
    fetch('/get_other_names')
        .then(response => response.json())
        .then(otherNames => {
            const otherNamesDropdown = document.getElementById('otherNamesDropdown');
            otherNames.forEach(name => {
                const option = document.createElement('option');
                option.value = name;
                option.textContent = name;
                otherNamesDropdown.appendChild(option);
            });

            // Event listener for other names dropdown
            otherNamesDropdown.addEventListener('change', function() {
                const selectedName = this.value;
                document.getElementById('ttsVoice').value = selectedName;
            });
        });
});





let ttsBlobs = {}; // Object to store blobs keyed by their text
let currentSelectedWavKey = null; // Store the key of the currently selected wav



document.getElementById('makeTube').addEventListener('click', function() {
    var youtubeLink = document.getElementById('youtubeLink').value;

    fetch('/make_tube', {
        method: 'POST',
        body: JSON.stringify({ youtube_link: youtubeLink }),
        headers: {
            'Content-Type': 'application/json'
        }
    })
    .then(response => response.json())
    .then(fileUrls => {
        fileUrls.forEach(url => {
            let filename = url.split('/').pop();
            fetch(url)
            .then(response => response.blob())
            .then(blob => {
                ttsBlobs[filename] = blob;
                addWavToList(filename); // Use the same function for adding to the list
            });
        });
    })
    .catch(error => console.error('Error:', error));
});

function addWavToList(filename) {
    var listItem = document.createElement('li');
    listItem.textContent = filename;
    listItem.dataset.textKey = filename;

    listItem.addEventListener('click', function() {
        currentSelectedWavKey = this.dataset.textKey;
        document.querySelectorAll('#wavList li').forEach(li => li.classList.remove('selected'));
        this.classList.add('selected');
        var audioPlayer = document.getElementById('audioPlayer');
        audioPlayer.src = URL.createObjectURL(ttsBlobs[filename]);
        audioPlayer.style.display = 'block';
        document.getElementById('playWav').disabled = false;
        document.getElementById('downloadWav').disabled = false;
    });

    document.getElementById('wavList').appendChild(listItem);
}



document.getElementById('generateTTS').addEventListener('click', function(event) {
    event.preventDefault(); // Prevent default form submission

    var text = document.getElementById('ttsText').value;
    var modelPath = document.getElementById('ttsModelPath').value;
    var fileIndex = document.getElementById('ttsFileIndex').value;
    var f0UpKey = document.getElementById('ttsF0UpKey').value;
    var voice = document.getElementById('ttsVoice').value;
    var ifRVC = document.getElementById('ifRVC').checked;

    fetch('/make_tts', {
        method: 'POST',
        body: JSON.stringify({
            model_path: modelPath,
            file_index: fileIndex,
            f0_up_key: f0UpKey,
            text: text,
            voice: voice,
            if_RVC: ifRVC
        }),
        headers: {
            'Content-Type': 'application/json'
        }
    })
    .then(response => response.blob())
    .then(blob => {
        ttsBlobs[text] = blob;

        var listItem = document.createElement('li');
        listItem.textContent = text;
        listItem.dataset.textKey = text;

        listItem.addEventListener('click', function() {
            currentSelectedWavKey = this.dataset.textKey;
            document.querySelectorAll('#wavList li').forEach(li => {
                li.classList.remove('selected');
                li.textContent = li.dataset.textKey; // Reset text content
            });
            this.classList.add('selected');
            this.textContent = "→ " + text; // Add arrow indicator to the selected item

            document.getElementById('playWav').disabled = false;
            document.getElementById('downloadWav').disabled = false;
        });

        document.getElementById('wavList').appendChild(listItem);
    })
    .catch(error => console.error('Error:', error));
});

document.getElementById('playWav').addEventListener('click', function(event) {
    event.preventDefault(); // Prevent default behavior

    if (currentSelectedWavKey && ttsBlobs[currentSelectedWavKey]) {
        var blobUrl = URL.createObjectURL(ttsBlobs[currentSelectedWavKey]);
        var audioPlayer = document.getElementById('audioPlayer');
        audioPlayer.src = blobUrl;
        audioPlayer.play();
    }
});

document.getElementById('downloadWav').addEventListener('click', function(event) {
    event.preventDefault(); // Prevent default behavior

    if (currentSelectedWavKey && ttsBlobs[currentSelectedWavKey]) {
        var blobUrl = URL.createObjectURL(ttsBlobs[currentSelectedWavKey]);
        var a = document.createElement('a');
        a.href = blobUrl;
        a.download = currentSelectedWavKey; // Use the filename as the download name
        document.body.appendChild(a);
        a.click();
        document.body.removeChild(a);
    }
});





        document.getElementById('makeVideo').addEventListener('click', function() {
            var selectedImage = document.querySelector('#imageList li.selected img');
            if (!selectedImage) {
                alert('Please select an image from the list');
                return;
            }

            fetch(selectedImage.src)
                .then(response => response.blob())
                .then(blob => {
                    var formData = new FormData();
                    formData.append('file', blob, 'image.png');
                    // Fetch additional parameters from the input fields
                    formData.append('fps_id', document.getElementById('fpsId').value);
                    formData.append('num_frames', document.getElementById('numFrames').value);
                    formData.append('num_steps', document.getElementById('numSteps').value);
                    formData.append('seed', document.getElementById('seed').value);
                    formData.append('decoding_t', document.getElementById('decodingT').value);
                    formData.append('motion_bucket_id', document.getElementById('motionBucketId').value);

                    fetch('/make_video', {
                        method: 'POST',
                        body: formData
                    })
                    .then(response => response.blob())
                    .then(blob => {
                        var url = URL.createObjectURL(blob);
                        var videoPlayer = document.getElementById('videoPlayer');
                        videoPlayer.src = url;
                        videoPlayer.load();

                        let frameCaptured = false;

                        videoPlayer.onloadedmetadata = function() {
                            videoPlayer.currentTime = videoPlayer.duration;
                        };

                        videoPlayer.onseeked = function() {
                            if (!frameCaptured) {
                                var canvas = document.createElement('canvas');
                                canvas.width = videoPlayer.videoWidth;
                                canvas.height = videoPlayer.videoHeight;
                                var ctx = canvas.getContext('2d');
                                ctx.drawImage(videoPlayer, 0, 0, canvas.width, canvas.height);

                                var frameUrl = canvas.toDataURL();
                                addToImageList(frameUrl);
                                frameCaptured = true;
                            }
                        };

                        videoPlayer.onerror = function(e) {
                            console.error("Error loading video", e);
                            alert('Error loading video. Please try a different file or format.');
                        };

                        videoPlayer.play().catch(e => {
                            console.error("Error playing video", e);
                            alert('Error playing video. Please try a different file or format.');
                        });

                        // Add the video to the video list
                        addToVideoList(url);
                    })
                    .catch(error => {
                        console.error('Error:', error);
                        alert('Error processing video. Please try again.');
                    });
                });
        });

function addToImageList(imageUrl) {
    const listItem = document.createElement('li');
    const image = new Image();
    image.src = imageUrl;
    image.width = 50;
    image.addEventListener('click', () => {
        displayImageOnCanvas(imageUrl);
    });
    listItem.appendChild(image);
    imageList.appendChild(listItem);
}

function displayImageOnCanvas(imageUrl) {
    const image = new Image();
    image.src = imageUrl;
    image.onload = () => {
        const ctx = document.getElementById('imageCanvas').getContext('2d');
        ctx.clearRect(0, 0, ctx.canvas.width, ctx.canvas.height);
        ctx.drawImage(image, 0, 0, ctx.canvas.width, ctx.canvas.height);
    };
}
function addToVideoList(videoUrl) {
    const video = document.createElement('video');
    video.src = videoUrl;
    video.crossOrigin = "anonymous"; // If videos are loaded from another domain
    video.preload = "auto"; // Preload the video

    video.oncanplaythrough = function() {
        const canvas = document.createElement('canvas');
        canvas.width = video.videoWidth;
        canvas.height = video.videoHeight;
        const ctx = canvas.getContext('2d');
        ctx.drawImage(video, 0, 0, canvas.width, canvas.height);

        const img = document.createElement('img');
        img.src = canvas.toDataURL();
        img.width = 100;
        img.style.cursor = "pointer"; // Change cursor to indicate it's clickable
        img.addEventListener('click', function() {
            playVideoInMainPlayer(videoUrl);
        });

        const listItem = document.createElement('li');
        listItem.appendChild(img);
        document.getElementById('videoList').appendChild(listItem);
    };
}

function playVideoInMainPlayer(videoUrl) {
    const mainVideoPlayer = document.getElementById('videoPlayer');
    mainVideoPlayer.src = videoUrl;
    mainVideoPlayer.load();
    mainVideoPlayer.play();
}




function addToImageList(imageUrl) {
    const listItem = document.createElement('li');
    const image = new Image();
    image.src = imageUrl;
    image.width = 50;
    image.addEventListener('click', () => {
        displayImageOnCanvas(imageUrl);
    });
    listItem.appendChild(image);
    imageList.appendChild(listItem);
}

function displayImageOnCanvas(imageUrl) {
    const image = new Image();
    image.src = imageUrl;
    image.onload = () => {
        const ctx = document.getElementById('imageCanvas').getContext('2d');
        ctx.clearRect(0, 0, ctx.canvas.width, ctx.canvas.height);
        ctx.drawImage(image, 0, 0, ctx.canvas.width, ctx.canvas.height);
    };
}





  // Event listener to mark an image as selected when clicked
    document.getElementById('imageList').addEventListener('click', function(e) {
        if (e.target.tagName === 'IMG') {
            // Remove 'selected' class from all images
            var images = this.getElementsByTagName('img');
            for (var i = 0; i < images.length; i++) {
                images[i].parentElement.classList.remove('selected');
            }
            // Add 'selected' class to the clicked image
            e.target.parentElement.classList.add('selected');
        }
    });






    // Function to fetch LoRA paths and populate the dropdown
    function fetchAndPopulateLoraPaths() {
        fetch('/get_lora_paths')
            .then(response => response.json())
            .then(data => {
                const dropdown = document.getElementById('loraPathsDropdown');
                for (const [name, path] of Object.entries(data)) {
                    const option = document.createElement('option');
                    option.value = path;
                    option.textContent = name;
                    dropdown.appendChild(option);
                }

                // Add event listener to the dropdown
                dropdown.addEventListener('change', function() {
                    // Update the loraPath textbox with the selected dropdown value
                    document.getElementById('loraPath').value = this.value;
                });
            })
            .catch(error => console.error('Error:', error));
    }

    // Call the function on page load
    fetchAndPopulateLoraPaths();
function drawOnObjectCanvas(mouseX, mouseY, width, height, rotation) {
    const x = mouseX - (width / 2);
    const y = mouseY - (height / 2);

    objectCtx.save(); // Save the current state of the canvas
    objectCtx.translate(x + width / 2, y + height / 2); // Move the canvas origin to the center of the image
    objectCtx.rotate(rotation * Math.PI / 180); // Rotate the canvas
    objectCtx.drawImage(canvas, -width / 2, -height / 2, width, height); // Draw the image
    objectCtx.restore(); // Restore the canvas to its original state
}

    let isShiftKeyPressed = false; // New global variable to track Shift key state

function autoDraw() {
    if (isDrawing && lastMouseX !== null && lastMouseY !== null) {
        let growAmount = parseInt(growOverTimeAmountInput.value);
        let rotateAmount = parseInt(rotateOverTimeAmountInput.value);

        if (isShiftKeyPressed) {
            growAmount *= -1;
            rotateAmount *= -1;
        }

        if (growOverTimeCheckbox.checked) {
            currentWidth += growAmount;
            currentHeight += growAmount;
        }
        if (rotateOvertimeCheckbox.checked) {
            currentRotation += rotateAmount; // Ensure this is updating correctly
        }

        drawOnObjectCanvas(lastMouseX, lastMouseY, currentWidth, currentHeight, currentRotation);
    }
}


    // Event listeners for auto drawing
    objectCanvas.addEventListener('mousedown', function(e) {
        isDrawing = true;
        const rect = objectCanvas.getBoundingClientRect();
        lastMouseX = e.clientX - rect.left;
        lastMouseY = e.clientY - rect.top;
        currentWidth = parseInt(startWidthInput.value);
        currentHeight = parseInt(startHeightInput.value);
        currentRotation = parseInt(startRotationInput.value);
        isShiftKeyPressed = e.shiftKey;
        autoDrawInterval = setInterval(autoDraw, parseInt(autoPlaceMsInput.value));
    });

    objectCanvas.addEventListener('mousemove', function(e) {
        isShiftKeyPressed = e.shiftKey; // Update Shift key state
        if (isDrawing && autoPlaceCheckbox.checked) {
            const rect = objectCanvas.getBoundingClientRect();
            lastMouseX = e.clientX - rect.left;
            lastMouseY = e.clientY - rect.top;
        }
    });

    document.addEventListener('keydown', function(e) {
        if (e.key === 'Shift') {
            isShiftKeyPressed = true;
        }
    });

    document.addEventListener('keyup', function(e) {
        if (e.key === 'Shift') {
            isShiftKeyPressed = false;
        }
    });

    objectCanvas.addEventListener('mouseup', endDrawing);
    objectCanvas.addEventListener('mouseleave', endDrawing);

    function endDrawing() {
        clearInterval(autoDrawInterval);
        isDrawing = false;
        lastMouseX = null;
        lastMouseY = null;
        currentWidth = parseInt(startWidthInput.value);
        currentHeight = parseInt(startHeightInput.value);
        currentRotation = parseInt(startRotationInput.value);
    }


    // Event listener to change canvas size
    document.getElementById('setCanvasSize').addEventListener('click', function() {
        var newWidth = parseInt(document.getElementById('canvasWidth').value);
        var newHeight = parseInt(document.getElementById('canvasHeight').value);
        var imageCanvas = document.getElementById('imageCanvas');
        var objectCanvas = document.getElementById('objectCanvas');

        imageCanvas.width = newWidth;
        imageCanvas.height = newHeight;
        objectCanvas.width = newWidth;
        objectCanvas.height = newHeight;
    });
objectCanvas.addEventListener('click', function(e) {
    if (!isDrawing) { // Regular drawing only if auto-draw is not active
        const rect = objectCanvas.getBoundingClientRect();
        const mouseX = e.clientX - rect.left;
        const mouseY = e.clientY - rect.top;

        // Get current rotation value
        const currentRotation = parseInt(document.getElementById('objectRotation').value);

        drawOnObjectCanvas(mouseX, mouseY, parseInt(objectWidthInput.value), parseInt(objectHeightInput.value), currentRotation);
    }
});


    saveDrawButton.addEventListener('click', function() {
        const drawnImage = new Image();
        drawnImage.src = objectCanvas.toDataURL();
        drawnImage.width = 50;

        const listItem = document.createElement('li');
        listItem.appendChild(drawnImage);
        imageList.appendChild(listItem);

        drawnImage.addEventListener('click', function() {
            ctx.clearRect(0, 0, canvas.width, canvas.height);
            ctx.drawImage(drawnImage, 0, 0, canvas.width, canvas.height);
        });
    });

    clearCanvasButton.addEventListener('click', function() {
        objectCtx.clearRect(0, 0, objectCanvas.width, objectCanvas.height);
        ctx.clearRect(0, 0, canvas.width, canvas.height);
    });

    document.getElementById('imageForm').addEventListener('submit', function(e) {
        e.preventDefault();

        var prompt = document.getElementById('prompt').value;
        var removebg = document.getElementById('removebg').checked;
        var width = document.getElementById('width').value;
        var height = document.getElementById('height').value;

        fetch('/generate_image', {
            method: 'POST',
            body: JSON.stringify({ prompt: prompt, remove_background: removebg, width: width, height: height }),
            headers: {
                'Content-Type': 'application/json'
            }
        })
        .then(response => response.blob())
        .then(blob => {
            var url = URL.createObjectURL(blob);
            displayImageOnCanvas(url);
            addToImageList(url);
        })
        .catch(error => console.error('Error:', error));
    });

document.getElementById('modifyImage').addEventListener('click', function() {
    var prompt = document.getElementById('modifyPrompt').value;
    var strength = parseFloat(document.getElementById('strength').value);
    var removeBackground = document.getElementById('modRemovebg').checked;
    var canvasData = canvas.toDataURL('image/jpeg').replace(/^data:image\/(png|jpeg);base64,/, "");
    var width = document.getElementById('width').value;
    var height = document.getElementById('height').value;

    fetch('/modify_image', {
        method: 'POST',
        body: JSON.stringify({ prompt: prompt, image: canvasData, strength: strength, remove_background: removeBackground, width: width, height: height }),
        headers: {
            'Content-Type': 'application/json'
        }
    })
    .then(response => response.blob())
    .then(blob => {
        var url = URL.createObjectURL(blob);

        // Display the modified image on the canvas
        displayImageOnCanvas(url);

        // Create a new list item with the modified image and add it to the image list
        var listItem = document.createElement('li');
        var img = new Image();
        img.src = url;
        img.width = 50; // Set a fixed width for the image in the list
        listItem.appendChild(img);
        imageList.appendChild(listItem);

        // Optional: Add a click event to the image in the list to display it on the canvas when clicked
        img.addEventListener('click', function() {
            displayImageOnCanvas(url);
        });
    })
    .catch(error => console.error('Error:', error));
});



// Add an event listener to the 'uploadImage' button
document.getElementById('uploadImage').addEventListener('click', function() {
    var imageUploadInput = document.getElementById('imageUpload');

    if (imageUploadInput.files && imageUploadInput.files[0]) {
        var reader = new FileReader();

        reader.onload = function(e) {
            var uploadedImage = new Image();
            uploadedImage.src = e.target.result;
            uploadedImage.width = 50;

            const listItem = document.createElement('li');
            listItem.appendChild(uploadedImage);
            imageList.appendChild(listItem);

            uploadedImage.addEventListener('click', function() {
                ctx.clearRect(0, 0, canvas.width, canvas.height);
                ctx.drawImage(uploadedImage, 0, 0, canvas.width, canvas.height);
            });
        };

        reader.readAsDataURL(imageUploadInput.files[0]);
    }
});


    function displayImageOnCanvas(imageUrl) {
        const image = new Image();
        image.src = imageUrl;
        image.onload = () => {
            ctx.clearRect(0, 0, canvas.width, canvas.height);
            ctx.drawImage(image, 0, 0, canvas.width, canvas.height);
        };
    }

    function addToImageList(imageUrl) {
        const listItem = document.createElement('li');
        const image = new Image();
        image.src = imageUrl;
        image.width = 50;
        image.addEventListener('click', () => {
            displayImageOnCanvas(imageUrl);
        });
        listItem.appendChild(image);
        imageList.appendChild(listItem);
    }




    document.getElementById('selectModel').addEventListener('click', function() {
        var loraPath = document.getElementById('loraPath').value;
        var loraScale = parseFloat(document.getElementById('loraScale').value);
        var modelType = document.getElementById('modelType').value;

        fetch('/select_model', {
            method: 'POST',
            body: JSON.stringify({ lora_filepath: loraPath, lora_scale: loraScale, pipeline_type: modelType }),
            headers: {
                'Content-Type': 'application/json'
            }
        })
        .then(response => response.json())
        .then(data => console.log('Success:', data))
        .catch(error => console.error('Error:', error));
    });

    document.getElementById('changePipeline').addEventListener('click', function() {
        var modelName = document.getElementById('modelName').value;
        var pipelineType = document.getElementById('pipelineType').value;

        fetch('/change_pipe', {
            method: 'POST',
            body: JSON.stringify({ model_name: modelName, pipeline_type: pipelineType }),
            headers: {
                'Content-Type': 'application/json'
            }
        })
        .then(response => response.json())
        .then(data => console.log('Success:', data))
        .catch(error => console.error('Error:', error));
    });
</script>

</body>
</html>


## Place your RVC models here i put some in as an example

In [ ]:
%%writefile /content/gooseygui/rvc_configurations.txt
toby, /content/drive/MyDrive/#BACKUPS/#voicervc/toby/toby.pth, /content/drive/MyDrive/#BACKUPS/#voicervc/toby/trained_IVF173_Flat_nprobe_1.index, 0
Patton_Oswalt, /content/drive/MyDrive/#BACKUPS/#voicervc/Patton_Oswalt/added_IVF558_Flat_nprobe_1_Patton_Oswalt_v2.index, /content/drive/MyDrive/#BACKUPS/#voicervc/Patton_Oswalt/Patton_Oswalt.pth, 0

Writing /content/gooseygui/rvc_configurations.txt


In [ ]:
!mv /content/tortoise-hf/tortoise-tts/tortoise/voices/daniel /content/tortoise-hf/tortoise-tts/tortoise/voices/dan

## Add the names of the voices u want to use located at /content/tortoise-hf/tortoise-tts/tortoise/voices

In [ ]:
%%writefile /content/gooseygui/other_names.txt
train_kennard
william
deniro
train_dotrice
pat
freeman
weaver
snakes
train_lescault
rainbow
angie
train_empire
Matt
myself
mol
train_daws
train_atkins
halle
scottaukerman
train_mouse
emma
lj
tim_reynolds
train_grace
geralt
applejack
train_dreams

Writing /content/gooseygui/other_names.txt


## create a list of all the names in /content/tortoise-hf/tortoise-tts/tortoise/voices

In [ ]:
import os

def list_directories(path):
    try:
        entries = os.listdir(path)
        directories = [entry for entry in entries if os.path.isdir(os.path.join(path, entry))]
        return directories
    except Exception as e:
        return f"An error occurred: {e}"

def write_directories_to_file(directories, file_path):
    try:
        with open(file_path, 'w') as file:
            for directory in directories:
                file.write(directory + '\n')
    except Exception as e:
        return f"Error writing to file: {e}"

# Directory to list
path_to_list = "/content/tortoise-hf/tortoise-tts/tortoise/voices"

# File to write to
output_file_path = "/content/directory_list.txt"

# List directories and write to file
directories = list_directories(path_to_list)
write_result = write_directories_to_file(directories, output_file_path)

if write_result:
    print(write_result)
else:
    print(f"Directories written to {output_file_path}")


Directories written to /content/directory_list.txt


# Run Goosey-GUI

In [ ]:
import torch
from flask import Flask, request, send_file, render_template, jsonify, send_from_directory
from diffusers import AutoPipelineForText2Image, AutoPipelineForImage2Image
from PIL import Image
import subprocess
import io
import base64
from pyngrok import ngrok
import json
import os
import cv2
import glob
import shutil
from werkzeug.utils import secure_filename
from pydub import AudioSegment
import logging
logging.basicConfig(level=logging.INFO)
from moviepy.editor import VideoFileClip, concatenate_videoclips


# Initialize the text-to-image pipeline
#pipe = AutoPipelineForText2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, variant="fp16").to("cuda")

# Initialize the image-to-image pipeline
#image2image_pipe = AutoPipelineForImage2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, use_safetensors=True)
#image2image_pipe.enable_model_cpu_offload()

# Define the template folder
template_dir = '/content/gooseygui'
app = Flask(__name__, template_folder=template_dir)

@app.route('/')
def index():
    return render_template('gooseygui.html')


@app.route('/append_audio', methods=['POST'])
def append_audio():
    audio_files = request.files.getlist('audio_files')

    combined_audio = None
    for audio_file in audio_files:
        audio_segment = AudioSegment.from_file(io.BytesIO(audio_file.read()))
        if combined_audio is None:
            combined_audio = audio_segment
        else:
            combined_audio += audio_segment  # Append instead of overlay

    if combined_audio is None:
        return "Failed to combine audio files", 500

    output_buffer = io.BytesIO()
    combined_audio.export(output_buffer, format='wav')
    output_buffer.seek(0)

    return send_file(
        output_buffer,
        as_attachment=True,
        mimetype='audio/wav',
        download_name='appended_audio.wav'
    )





def overlay_audios(audio_paths):
    combined = None
    for path in audio_paths:
        try:
            audio = AudioSegment.from_file(path)
            if combined is None:
                combined = audio
            else:
                combined = combined.overlay(audio)
        except Exception as e:
            print(f"Error processing {path}: {e}")
    return combined


@app.route('/make_audio', methods=['POST'])
def make_audio():
    audio_files = request.files.getlist('audio_files')

    combined_audio = None
    for audio_file in audio_files:
        audio_segment = AudioSegment.from_file(io.BytesIO(audio_file.read()))
        if combined_audio is None:
            combined_audio = audio_segment
        else:
            combined_audio = combined_audio.overlay(audio_segment)

    if combined_audio is None:
        return "Failed to combine audio files", 500

    output_buffer = io.BytesIO()
    combined_audio.export(output_buffer, format='wav')
    output_buffer.seek(0)

    return send_file(
        output_buffer,
        as_attachment=True,
        mimetype='audio/wav',
        download_name='combined_audio.wav'
    )



@app.route('/make_tube', methods=['POST'])
def make_tube():
    data = request.json
    youtube_link = data.get('youtube_link')
    if not youtube_link:
        return 'YouTube link is required', 400

    try:
        # Clear previous outputs
        subprocess.run(["rm", "-r", "/content/youtube_out"], check=True)
        subprocess.run(["rm", "-r", "/content/seperate_out"], check=True)

        # Run the processing scripts
        subprocess.run(["python", "/content/pytube_inf.py", youtube_link, "/content/youtube_out/audio.mp3", "mp3"], check=True)
        subprocess.run(["python", "/content/demuc.py"], check=True)
        subprocess.run(["python", "/content/mp3split.py"], check=True)

        # Assuming files are stored in '/content/seperate_out/htdemucs/audio/split'
        output_dir = '/content/seperate_out/htdemucs/audio/split'
        # Replace 'http' with 'https' in the generated file URLs
        file_urls = [request.url_root.replace('http://', 'https://') + 'audio_files/' + filename for filename in os.listdir(output_dir)]

        return jsonify(file_urls)

    except subprocess.CalledProcessError as e:
        return f"Error during processing: {e}", 500

    except Exception as e:
        return f"An error occurred: {e}", 500


@app.route('/audio_files/<filename>')
def get_audio_file(filename):
    return send_from_directory('/content/seperate_out/htdemucs/audio/split', filename)


@app.route('/rvc_convert', methods=['POST'])
def rvc_convert():
    %cd /content/

    if 'file' not in request.files:
        return 'No file part', 400

    file = request.files['file']
    input_file_path = '/content/out/daniel_0_0.wav'
    file.save(input_file_path)

    # Extract other required parameters
    model_path = request.form.get('model_path', 'default_model_path')
    file_index = request.form.get('file_index', 'default_file_index')
    f0_up_key = request.form.get('f0_up_key', '1')

    # Run the RVC script
    rvc_command = [
        "python", "/content/rvcscript.py", "--model_path", model_path,
        "--file_index", file_index, "--f0_up_key", f0_up_key
    ]

    try:
        subprocess.run(rvc_command, check=True)
        processed_file_path = "/content/output/out.wav"
        return send_file(processed_file_path, as_attachment=True)
    except subprocess.CalledProcessError as e:
        return f"Error during RVC processing: {e}", 500





@app.route('/make_song', methods=['POST'])
def make_song():
    data = request.json
    duration = data.get('duration', 30)  # Default duration to 30 seconds if not provided
    description = data.get('prompt', 'Default Music Description')

    try:
        # Install the audiocraft package
        subprocess.run(["pip", "install", "audiocraft"], check=True)

        # Generate the music file
        music_generation_command = [
            "python", "/content/music1.py",
            "--description", description,
            "--duration", str(duration),
            "--output_name", "/content/Audio_Out.wav"
        ]
        subprocess.run(music_generation_command, check=True)

        # Uninstall the audiocraft package
        subprocess.run(["pip", "uninstall", "audiocraft", "-y"], check=True)

        # Check if the audio file was successfully generated
        if os.path.exists("/content/Audio_Out.wav"):
            return send_file("/content/Audio_Out.wav", mimetype='audio/wav')
        else:
            return "Music generation failed, output file not found", 500

    except subprocess.CalledProcessError as e:
        return f"Error during music generation or package management: {e}", 500


@app.route('/wav2lip', methods=['POST'])
def wav2lip():
    if 'inputMedia' not in request.files or 'inputAudio' not in request.files:
        return "Missing files", 400

    os.chdir('/content/Wav2Lip')

    input_media = request.files['inputMedia']
    input_audio = request.files['inputAudio']

    if input_media.mimetype.startswith('image'):
        media_extension = '.jpg'
    elif input_media.mimetype.startswith('video'):
        media_extension = '.mp4'
    else:
        return "Unsupported media type", 400

    media_path = f'/content/input_media{media_extension}'
    audio_path = '/content/input_audio.wav'

    input_media.save(media_path)
    input_audio.save(audio_path)

    # If media is a video, process it to make it loopable
    if media_extension == '.mp4':
        loopable_video_path = make_loopable(media_path)
    else:
        loopable_video_path = media_path  # No processing needed for images

    # Run Wav2Lip inference
    result_path = '/content/Wav2Lip/results/result_voice.mp4'
    try:
        subprocess.run([
            'python', 'inference.py',
            '--checkpoint_path', 'checkpoints/wav2lip_gan.pth',
            '--face', loopable_video_path,
            '--audio', audio_path
        ], check=True)
    except subprocess.CalledProcessError as e:
        return f"Error during Wav2Lip inference: {e}", 500

    if os.path.exists(result_path):
        return send_file(result_path, mimetype='video/mp4')
    else:
        return "Inference failed, output file not found", 500

def make_loopable(video_path):
    cap = cv2.VideoCapture(video_path)
    frames = []

    while True:
        ret, frame = cap.read()
        if not ret:
            break
        frames.append(frame)

    cap.release()

    loopable_video_path = '/content/loopable_video.mp4'
    out = cv2.VideoWriter(loopable_video_path, cv2.VideoWriter_fourcc(*'mp4v'), 30, (frames[0].shape[1], frames[0].shape[0]))

    for frame in frames + frames[::-1]:  # Write frames in normal and reverse order
        out.write(frame)

    out.release()
    return loopable_video_path


@app.route('/get_lora_paths')
def get_lora_paths():
    try:
        with open('/content/gooseygui/loralist.txt') as file:
            lora_paths = json.load(file)
        return lora_paths
    except Exception as e:
        app.logger.error(f"Error reading loralist.txt: {e}")
        return {'error': str(e)}, 500


@app.route('/get_other_names')
def get_other_names():
    try:
        with open('/content/gooseygui/other_names.txt') as file:
            other_names = file.read().splitlines()
        return jsonify(other_names)
    except Exception as e:
        return jsonify({"error": str(e)})
@app.route('/get_rvc_configurations')
def get_rvc_configurations():
    try:
        with open('/content/gooseygui/rvc_configurations.txt') as file:
            configurations = [line.strip().split(', ') for line in file]
        return jsonify(configurations)
    except Exception as e:
        return jsonify({"error": str(e)})


@app.route('/make_tts', methods=['POST'])
def make_tts():


    data = request.json
    %cd /content/
    # Extract parameters from the request
    model_path = data.get('model_path', '/default/model/path')
    file_index = data.get('file_index', '/default/file/index')
    f0_up_key = data.get('f0_up_key', '1')
    text = data.get('text', 'default text')
    voice = data.get('voice', 'default voice')
    if_rvc = data.get('if_RVC', False)  # Extract the if_RVC flag

    # Change directory and install specific transformers version
    subprocess.run(["pip", "install", "transformers==4.19.0"], check=True)

    # Run the TTS script
    tts_command = [
        "python3", "/content/tortoise-hf/tortoise-tts/tortoise/do_tts.py",
        "--text", text, "--voice", voice, "--preset", "high_quality",
        "--output", "/content/out/"
    ]
    try:
        subprocess.run(tts_command, check=True)
    except subprocess.CalledProcessError as e:
        return f"Error during TTS generation: {e}", 500
    tts_file_path = f"/content/out/{voice}_0_0.wav"
    dynamic_file_path = f"/content/out/{voice}_0_0.wav"
    target_file_path = "/content/out/daniel_0_0.wav"

    dynamic_file_path = f"/content/out/{voice}_0_0.wav"

    # Set the target filename
    target_file_path = "/content/out/daniel_0_0.wav"

    # Execute the copy command
    subprocess.run(["cp", dynamic_file_path, target_file_path], check=True)
    # Run the RVC script if if_RVC is True
    if if_rvc:
        %cd /content/
        rvc_command = [
            "python", "/content/rvcscript.py", "--model_path", model_path,
            "--file_index", file_index, "--f0_up_key", f0_up_key
        ]
        try:
            subprocess.run(rvc_command, check=True)
        except subprocess.CalledProcessError as e:
            return f"Error during RVC processing: {e}", 500
        tts_file_path = "/content/output/out.wav"


    # Send the generated TTS file
    return send_file(tts_file_path, as_attachment=True)





@app.route('/make_video', methods=['POST'])
def make_video():
    %cd /content/generative-models

    # Check if the POST request has the file part
    if 'file' not in request.files:
        return "No file part", 400

    file = request.files['file']

    # If the user does not select a file, the browser submits an empty part without a filename
    if file.filename == '':
        return "No selected file", 400

    # Optional parameters with default values
    fps_id = request.form.get('fps_id', '30')
    num_frames = request.form.get('num_frames', '25')
    num_steps = request.form.get('num_steps', '30')
    seed = request.form.get('seed', '23')
    decoding_t = request.form.get('decoding_t', '5')
    motion_bucket_id = request.form.get('motion_bucket_id', '100')

    if file:
        # Delete existing files, use os.remove in Python script
        if os.path.exists("/content/outVid/000000.mp4"):
            os.remove("/content/outVid/000000.mp4")
        if os.path.exists("/content/outVid/converted_000000.mp4"):
            os.remove("/content/outVid/converted_000000.mp4")

        input_image_path = "/content/sdog.png"
        output_video_path = "/content/outVid/000000.mp4"
        output_converted_video_path = "/content/outVid/converted_000000.mp4"
        output_folder = "/content/outVid/"

        # Save the image file
        file.save(input_image_path)

        # Create output directory if not exists
        if not os.path.exists(output_folder):
            os.makedirs(output_folder)

        # Prepare the command with optional arguments
        command = [
            "python", "/content/generative-models/scripts/sampling/simple_video_sample.py",
            "--version=svd_xt", "--input_path=" + input_image_path,
            "--fps_id", fps_id, "--num_frames", num_frames,
            "--num_steps", num_steps, "--seed", seed,
            "--decoding_t", decoding_t, "--motion_bucket_id", motion_bucket_id,
            "--output_folder=" + output_folder
        ]

        # Run the video generation script
        try:
            subprocess.run(command, check=True)
        except subprocess.CalledProcessError as e:
            return f"Error during video generation: {e}", 500

        # Convert the video format using FFmpeg
        try:
            ffmpeg_command = [
                'ffmpeg',
                '-i', output_video_path,
                '-vcodec', 'libx264',
                '-acodec', 'aac',
                '-strict', '-2',
                output_converted_video_path
            ]
            subprocess.run(ffmpeg_command, check=True)
        except subprocess.CalledProcessError as e:
            return f"Error during video conversion: {e}", 500

        # Send the converted video file back
        return send_file(output_converted_video_path, mimetype='video/mp4')


@app.route('/generate_image', methods=['POST'])
def generate_image():
    data = request.json
    prompt = data.get('prompt', 'a default prompt')
    remove_background = data.get('remove_background', False)
    width = int(data.get('width', 512))  # Default width to 512 if not provided
    height = int(data.get('height', 512))  # Default height to 512 if not provided

    # Ensure width and height are multiples of 8
    if width % 8 != 0 or height % 8 != 0:
        return {"error": "Width and height must be multiples of 8."}, 400

    image = pipe(prompt=prompt, num_inference_steps=100, guidance_scale=7.5, width=width, height=height).images[0]

    temp_image_path = "/content/temp_generated_image.png"
    image.save(temp_image_path, format='PNG')

    if remove_background:
        output_image_path = "/content/bgremoved.png"
        result = subprocess.run(["python", "/content/background-replacement-hf/removebg.py", temp_image_path, output_image_path], capture_output=True, text=True)
        image_path_to_send = output_image_path
    else:
        image_path_to_send = temp_image_path

    return send_file(image_path_to_send, mimetype='image/png')

@app.route('/modify_image', methods=['POST'])
def modify_image():
    data = request.json
    prompt = data['prompt']
    image_data = base64.b64decode(data['image'])
    remove_background = data.get('remove_background', False)
    strength = data.get('strength', 0.27)
    width = data.get('width', 512)
    height = data.get('height', 512)

    init_image = Image.open(io.BytesIO(image_data))
    generated_image = image2image_pipe(prompt, image=init_image, strength=strength, steps=100, width=width, height=height).images[0]

    if remove_background:
        temp_image_path = "/content/temp_modified_image.png"
        generated_image.save(temp_image_path, format='PNG')
        output_image_path = "/content/bgremoved_modified.png"
        %cd /content/background-replacement-hf
        result = subprocess.run(["python", "/content/background-replacement-hf/removebg.py", temp_image_path, output_image_path], capture_output=True, text=True)
        image_path_to_send = output_image_path
    else:
        img_byte_arr = io.BytesIO()
        generated_image.save(img_byte_arr, format='JPEG')
        img_byte_arr.seek(0)
        return send_file(img_byte_arr, mimetype='image/jpeg')

    return send_file(image_path_to_send, mimetype='image/png')

@app.route('/select_model', methods=['POST'])
def select_model():
    data = request.json
    lora_filepath = data['lora_filepath']
    pipeline_type = data['pipeline_type']  # 'TXT' or 'IMG'
    lora_scale = data.get('lora_scale', 1)  # Default lora_scale to 1 if not provided

    try:
        if pipeline_type == 'TXT':
            pipe.load_lora_weights(lora_filepath, weight_name=lora_filepath)
            pipe.fuse_lora(lora_scale=lora_scale)
            return {'message': 'LoRA weights loaded into text-to-image pipeline'}

        elif pipeline_type == 'IMG':
            image2image_pipe.load_lora_weights(lora_filepath, weight_name=lora_filepath)
            image2image_pipe.fuse_lora(lora_scale=lora_scale)
            return {'message': 'LoRA weights loaded into image-to-image pipeline'}

        else:
            return {'error': 'Invalid pipeline type specified'}, 400
    except Exception as e:
        return {'error': str(e)}, 500

@app.route('/change_pipe', methods=['POST'])
def change_pipe():
    data = request.json
    model_name = data['model_name']
    pipeline_type = data['pipeline_type']  # 'TXT' or 'IMG'
    global pipe, image2image_pipe
    try:
        if pipeline_type == 'TXT':
            pipe = AutoPipelineForText2Image.from_pretrained(model_name, torch_dtype=torch.float16, variant="fp16").to("cuda")
            return {'message': f'Text-to-image pipeline changed to model: {model_name}'}
        elif pipeline_type == 'IMG':
            image2image_pipe = AutoPipelineForImage2Image.from_pretrained(model_name, torch_dtype=torch.float16, use_safetensors=True)
            image2image_pipe.enable_model_cpu_offload()
            return {'message': f'Image-to-image pipeline changed to model: {model_name}'}
        else:
            return {'error': 'Invalid pipeline type specified'}, 400
    except Exception as e:
        return {'error': str(e)}, 500

def start_ngrok():
    ngrok_tunnel = ngrok.connect(5000)
    print('Ngrok Tunnel URL:', ngrok_tunnel.public_url)

if __name__ == '__main__':
    start_ngrok()
    app.run()


Ngrok Tunnel URL: https://b749-35-240-196-131.ngrok-free.app
 * Serving Flask app '__main__'
 * Debug mode: off


INFO:werkzeug:WARNING: This is a development server. Do not use it in a production deployment. Use a production WSGI server instead.
 * Running on http://127.0.0.1:5000
INFO:werkzeug:Press CTRL+C to quit
INFO:werkzeug:127.0.0.1 - - [31/Dec/2023 02:31:28] "GET / HTTP/1.1" 200 -
INFO:werkzeug:127.0.0.1 - - [31/Dec/2023 02:31:30] "GET /get_lora_paths HTTP/1.1" 200 -
INFO:werkzeug:127.0.0.1 - - [31/Dec/2023 02:31:30] "GET /get_rvc_configurations HTTP/1.1" 200 -
INFO:werkzeug:127.0.0.1 - - [31/Dec/2023 02:31:30] "GET /get_other_names HTTP/1.1" 200 -
INFO:werkzeug:127.0.0.1 - - [31/Dec/2023 02:31:30] "GET /favicon.ico HTTP/1.1" 404 -


# ~~~~~~~

# ~~~~~~~

# ~~~~~~~

# ~~~~~~~

# ~~~~~~~

# ~~~~~~~

# ~~~~~~~

# ~~~~~~~

# ~~~~~~~

# Install TTS_ voices from MP3 samples

In [ ]:
import zipfile
import os

zip_file_path = "/content/drive/MyDrive/#BACKUPS/tts samps.zip"
extract_to_path = "/content/#voicemp3"

# Create the target directory if it doesn't exist
if not os.path.exists(extract_to_path):
    os.makedirs(extract_to_path)
    print(f"Created directory: {extract_to_path}")

# Extract the zip file
try:
    with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
        zip_ref.extractall(extract_to_path)
    print(f"Extracted '{zip_file_path}' to '{extract_to_path}'")
except Exception as e:
    print(f"An error occurred: {e}")


In [ ]:
!pip install pydub
from pydub import AudioSegment
import os

# Iterate over all mp3 files in the source directory
for filename in os.listdir("/content/#voicemp3"):
    if filename.endswith(".mp3"):
        # Load the MP3 file
        audio_path = os.path.join("/content/#voicemp3", filename)
        audio = AudioSegment.from_mp3(audio_path)

        # Define the duration for each segment in milliseconds (10 seconds = 10000 milliseconds)
        duration_per_segment = 10000

        # Calculate the number of segments
        num_segments = len(audio) // duration_per_segment + (1 if len(audio) % duration_per_segment else 0)

        # Create a new directory for the split files, named after the mp3 file
        new_dir = os.path.join("/content/tortoise-hf/tortoise-tts/tortoise/voices", filename.rsplit(".", 1)[0])
        os.makedirs(new_dir, exist_ok=True)

        # Split the audio and save each segment
        for i in range(num_segments):
            start_time = i * duration_per_segment
            end_time = (i+1) * duration_per_segment
            segment = audio[start_time:end_time]
            segment.export(f"{new_dir}/{i+1}.wav", format="wav")
            print(f"Saved segment {i+1}.wav for {filename}")

print("All segments saved successfully!")


# demurc

In [ ]:
!python3 -m pip install -U git+https://github.com/facebookresearch/demucs#egg=demucs


In [ ]:
!pip install pytube

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 kB 1.6 MB/s eta 0:00:00


In [ ]:
%%writefile /content/pytube_inf.py
import os
import pytube
import subprocess
import argparse

def download_video(youtube_link, output_file_path, format):
    try:
        yt = pytube.YouTube(youtube_link)

        # Ensure the directory exists
        output_directory = os.path.dirname(output_file_path)
        if not os.path.exists(output_directory):
            os.makedirs(output_directory)

        if format == "mp3":
            stream = yt.streams.filter(only_audio=True).first()
            if not stream:
                raise ValueError("No audio stream found")

            # Download the video
            temp_video_path = stream.download(output_directory)

            # Convert to MP3
            subprocess.run(["ffmpeg", "-i", temp_video_path, output_file_path])
            os.remove(temp_video_path)  # Delete the original video file
            print("Audio converted and saved as MP3 successfully!")
        else:
            raise ValueError("This script currently only supports MP3 format")

    except Exception as e:
        print(f"An error occurred: {e}")

if __name__ == "__main__":
    parser = argparse.ArgumentParser(description='Download YouTube videos as MP3.')
    parser.add_argument('youtube_link', type=str, help='YouTube video link')
    parser.add_argument('output_file_path', type=str, help='Full path for the output MP3 file')
    parser.add_argument('format', type=str, choices=['mp3'], help='Download format (currently only supports mp3)')

    args = parser.parse_args()

    download_video(args.youtube_link, args.output_file_path, args.format)


Overwriting /content/pytube_inf.py


In [ ]:
!python /content/pytube_inf.py https://www.youtube.com/watch?v=MA4a21YNzss /content/youtube_out/audio.mp3 mp3


ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

In [ ]:
!rm  -r /content/youtube_out
!rm -r /content/seperate_out
!python /content/pytube_inf.py https://www.youtube.com/watch?v=MA4a21YNzss /content/youtube_out/audio.mp3 mp3
!python /content/demuc.py
!python /content/mp3split.py

rm: cannot remove '/content/youtube_out': No such file or directory
ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libt

In [ ]:
%%writefile /content/mp3split.py
from pydub import AudioSegment
import os

def split_mp3_to_mono_wav(source_folder, target_folder, segment_length=60 * 1000):  # 60 * 1000 ms = 1 minute
    if not os.path.exists(target_folder):
        os.makedirs(target_folder)

    for filename in os.listdir(source_folder):
        if filename.endswith(".mp3"):
            path = os.path.join(source_folder, filename)
            audio = AudioSegment.from_mp3(path)

            # Calculate the number of segments
            length_audio = len(audio)
            total_segments = length_audio // segment_length + (1 if length_audio % segment_length else 0)

            for i in range(total_segments):
                start_time = i * segment_length
                end_time = min(start_time + segment_length, length_audio)

                split_audio = audio[start_time:end_time]
                # Convert to mono
                split_audio = split_audio.set_channels(1)
                split_filename = f"{os.path.splitext(filename)[0]}_{i}.wav"
                split_audio.export(os.path.join(target_folder, split_filename), format="wav")

# Replace '/content/seperate_out/htdemucs/audio' with the path to your source mp3 files
# Replace '/content/seperate_out/htdemucs/audio/split' with the path where you want to save the split files
source_folder = '/content/seperate_out/htdemucs/audio'
target_folder = '/content/seperate_out/htdemucs/audio/split'

split_mp3_to_mono_wav(source_folder, target_folder)


Overwriting /content/mp3split.py


In [ ]:
%%writefile /content/demuc.py
# Customize the following options!
model = "htdemucs"
extensions = ["mp3", "wav", "ogg", "flac"]  # we will look for all those file types.
two_stems = None   # only separate one stems from the rest, for instance
# two_stems = "vocals"

# Options for the output audio.
mp3 = True
mp3_rate = 320
float32 = False  # output as float 32 wavs, unsused if 'mp3' is True.
int24 = False    # output as int24 wavs, unused if 'mp3' is True.
# You cannot set both `float32 = True` and `int24 = True` !!

in_path = '/content/youtube_out/'
out_path = '/content/seperate_out/'
import io
from pathlib import Path
import select
from shutil import rmtree
import subprocess as sp
import sys
from typing import Dict, Tuple, Optional, IO

from google.colab import files

def find_files(in_path):
    out = []
    for file in Path(in_path).iterdir():
        if file.suffix.lower().lstrip(".") in extensions:
            out.append(file)
    return out

def copy_process_streams(process: sp.Popen):
    def raw(stream: Optional[IO[bytes]]) -> IO[bytes]:
        assert stream is not None
        if isinstance(stream, io.BufferedIOBase):
            stream = stream.raw
        return stream

    p_stdout, p_stderr = raw(process.stdout), raw(process.stderr)
    stream_by_fd: Dict[int, Tuple[IO[bytes], io.StringIO, IO[str]]] = {
        p_stdout.fileno(): (p_stdout, sys.stdout),
        p_stderr.fileno(): (p_stderr, sys.stderr),
    }
    fds = list(stream_by_fd.keys())

    while fds:
        # `select` syscall will wait until one of the file descriptors has content.
        ready, _, _ = select.select(fds, [], [])
        for fd in ready:
            p_stream, std = stream_by_fd[fd]
            raw_buf = p_stream.read(2 ** 16)
            if not raw_buf:
                fds.remove(fd)
                continue
            buf = raw_buf.decode()
            std.write(buf)
            std.flush()

def separate(inp=None, outp=None):
    inp = inp or in_path
    outp = outp or out_path
    cmd = ["python3", "-m", "demucs.separate", "-o", str(outp), "-n", model]
    if mp3:
        cmd += ["--mp3", f"--mp3-bitrate={mp3_rate}"]
    if float32:
        cmd += ["--float32"]
    if int24:
        cmd += ["--int24"]
    if two_stems is not None:
        cmd += [f"--two-stems={two_stems}"]
    files = [str(f) for f in find_files(inp)]
    if not files:
        print(f"No valid audio files in {in_path}")
        return
    print("Going to separate the files:")
    print('\n'.join(files))
    print("With command: ", " ".join(cmd))
    p = sp.Popen(cmd + files, stdout=sp.PIPE, stderr=sp.PIPE)
    copy_process_streams(p)
    p.wait()
    if p.returncode != 0:
        print("Command failed, something went wrong.")


def from_upload():
    out_path = Path('separated')
    in_path = Path('tmp_in')

    if in_path.exists():
        rmtree(in_path)
    in_path.mkdir()

    if out_path.exists():
        rmtree(out_path)
    out_path.mkdir()

    uploaded = files.upload()
    for name, content in uploaded.items():
        (in_path / name).write_bytes(content)
    separate(in_path, out_path)

separate()

Writing /content/demuc.py


In [ ]:
!pip install audiocraft
!python /content/music1.py --description "Heavy Metal Music" --duration 30 --output_name "/content/Audio_Out.wav"
!pip uninstall audiocraft -y

  Using cached audiocraft-1.1.0-py3-none-any.whl
  Using cached hydra_core-1.3.2-py3-none-any.whl (154 kB)
  Using cached typer-0.7.0-py3-none-any.whl (38 kB)
  Using cached omegaconf-2.3.0-py3-none-any.whl (79 kB)
  Using cached antlr4_python3_runtime-4.9.3-py3-none-any.whl
  Attempting uninstall: antlr4-python3-runtime
    Found existing installation: antlr4-python3-runtime 4.8
    Uninstalling antlr4-python3-runtime-4.8:
      Successfully uninstalled antlr4-python3-runtime-4.8
  Attempting uninstall: typer
    Found existing installation: typer 0.9.0
    Uninstalling typer-0.9.0:
      Successfully uninstalled typer-0.9.0
  Attempting uninstall: omegaconf
    Found existing installation: omegaconf 2.0.6
    Uninstalling omegaconf-2.0.6:
      Successfully uninstalled omegaconf-2.0.6
  Attempting uninstall: hydra-core
    Found existing installation: hydra-core 1.0.7
    Uninstalling hydra-core-1.0.7:
      Successfully uninstalled hydra-core-1.0.7
ERROR: pip's dependency resolver d

2023-12-30 03:14:50.048159: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-30 03:14:50.048213: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-30 03:14:50.049703: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-30 03:14:51.350385: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecate

# wav2lip

In [ ]:
#!pip install -q torch==1.13.1+cu116 torchvision==0.14.1+cu116 torchaudio==0.13.1 torchtext==0.14.1 torchdata==0.5.1 --extra-index-url https://download.pytorch.org/whl/cu116 -U
!git clone https://huggingface.co/camenduru/Wav2Lip
#!pip install gradio yt_dlp ffmpeg-python librosa==0.8.0
%cd /content/Wav2Lip

Cloning into 'Wav2Lip'...
remote: Enumerating objects: 72, done.
remote: Counting objects: 100% (3/3), done.
remote: Compressing objects: 100% (3/3), done.
remote: Total 72 (delta 0), reused 0 (delta 0), pack-reused 69
Unpacking objects: 100% (72/72), 442.42 KiB | 848.00 KiB/s, done.
Filtering content: 100% (6/6), 936.88 MiB | 172.39 MiB/s, done.
/content/Wav2Lip


In [ ]:
!python inference.py --checkpoint_path checkpoints/wav2lip_gan.pth --face "/content/testing.mp4" --audio "/content/testing.wav"

Using cuda for inference.
Reading video frames...
Number of frames available for inference: 110
/content/Wav2Lip/audio.py:100: FutureWarning: Pass sr=16000, n_fft=800 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  return librosa.filters.mel(hp.sample_rate, hp.n_fft, n_mels=hp.num_mels,
(80, 193)
Length of mel chunks: 57
  0% 0/1 [00:00<?, ?it/s]
  0% 0/4 [00:00<?, ?it/s]
 25% 1/4 [00:01<00:05,  1.76s/it]
 50% 2/4 [00:01<00:01,  1.19it/s]
 75% 3/4 [00:02<00:00,  1.86it/s]
100% 4/4 [00:03<00:00,  1.19it/s]
Load checkpoint from: checkpoints/wav2lip_gan.pth
Model loaded
100% 1/1 [00:05<00:00,  5.07s/it]
ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enab

In [ ]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('/content/Wav2Lip/results/result_voice.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML(f"""
<video width="50%" height="50%" controls>
      <source src="{data_url}" type="video/mp4">
</video>""")

# MusicGen

In [ ]:
%cd /content/
!pip install -U audiocraft

/content
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 610.4/610.4 kB 9.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 51.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.4/72.4 kB 11.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.5/154.5 kB 17.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.6/59.6 kB 8.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.3/143.3 kB 19.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 75.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.6/6.6 MB 80.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 

In [ ]:
# Best to make sure you have torch installed first, in particular before installing xformers.
# Don't run this if you already have PyTorch installed.
#!pip install 'torch>=2.0'
# Then proceed to one of the following
#!pip install -U audiocraft  # stable release
#!pip install -U git+https://git@github.com/facebookresearch/audiocraft#egg=audiocraft  # bleeding edge
#!pip install -e .  # or if you cloned the repo locally (mandatory if you want to train).

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 610.4/610.4 kB 10.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 50.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.4/72.4 kB 10.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.5/154.5 kB 22.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.6/59.6 kB 9.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.3/143.3 kB 21.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 76.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.6/6.6 MB 94.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.0/21

  Cloning https://****@github.com/facebookresearch/audiocraft to /tmp/pip-install-a3uk8r7e/audiocraft_36ac48317b8d4d40a1e5adb5616f20d6
  Running command git clone --filter=blob:none --quiet 'https://****@github.com/facebookresearch/audiocraft' /tmp/pip-install-a3uk8r7e/audiocraft_36ac48317b8d4d40a1e5adb5616f20d6
  Resolved https://****@github.com/facebookresearch/audiocraft to commit e1f2b18f89210ab5a71bc0d31d156d84a8280d9f
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.6/6.6 MB 55.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.1/50.1 kB 76.7 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.0/45.0 kB 6.3 MB/s eta 0:00:00
  Created wheel for audiocraft: filename=audiocraft-1.2.0a2-py3-none-any.whl size=275213 sha256=ccf545b07437a01c9880ac494d45c9d3904399cd19076522cdefc164196602da
  Stored in directory: /tmp/pip-ephem-wheel-cache-nb7h8k6l/wheels/61/bb/15/cf53514254501b4472fb64d137bd3ab88737daf6917dfcbdc9
Succ

In [ ]:
#!pip uninstall fairseq torchdata torchtext torchvision -y
#!pip install fairseq torchdata torchtext torchvision

  Using cached fairseq-0.12.2-cp310-cp310-linux_x86_64.whl
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 43.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 85.8 MB/s eta 0:00:00
  Using cached torchvision-0.16.2-cp310-cp310-manylinux1_x86_64.whl (6.8 MB)
  Using cached hydra_core-1.0.7-py3-none-any.whl (123 kB)
  Using cached omegaconf-2.0.6-py3-none-any.whl (36 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 670.2/670.2 MB 2.1 MB/s eta 0:00:00
  Using cached antlr4_python3_runtime-4.8-py3-none-any.whl
INFO: pip is looking at multiple versions of torchaudio to determine which version is compatible with other requirements. This could take a while.
  Using cached torchaudio-2.1.2-cp310-cp310-manylinux1_x86_64.whl (3.3 MB)
  Attempting uninstall: antlr4-python3-runtime
    Found existing installation: antlr4-python3-runtime 4.9.3
    Uninstalling antlr4-python3-runtime-4.9.3:
      Successfully uninstalled antlr4-python3-runtime-4.9.3
  Attempting 

In [ ]:
%%writefile /content/music1.py
import argparse
from audiocraft.models import MusicGen, MultiBandDiffusion
import soundfile as sf
from audiocraft.utils.notebook import display_audio

# Initialize the MusicGen model
USE_DIFFUSION_DECODER = False
model = MusicGen.get_pretrained('facebook/musicgen-large')
if USE_DIFFUSION_DECODER:
    mbd = MultiBandDiffusion.get_mbd_musicgen()

# Function to generate music
def generate_music(description, duration, output_name):
    # Set generation parameters
    model.set_generation_params(
        use_sampling=True,
        top_k=250,
        duration=duration
    )

    # Generate music
    output = model.generate(
        descriptions=[description],
        progress=True, return_tokens=True
    )

    # Process and save the audio
    audio_data_cpu = output[0].cpu().numpy().reshape(-1)
    sf.write(output_name, audio_data_cpu, 32000)

    # Display the audio (comment this out if running in a non-interactive environment)
    # display_audio(output[0], sample_rate=32000)

    # Additional code for diffusion decoder, if used
    if USE_DIFFUSION_DECODER:
        out_diffusion = mbd.tokens_to_wav(output[1])
        # display_audio(out_diffusion, sample_rate=32000)  # Comment out if non-interactive
        out_diffusion_cpu = out_diffusion.cpu().numpy().reshape(-1)
        sf.write(output_name.replace('.wav', '_Diffusion.wav'), out_diffusion_cpu, 32000)

# Set up argument parser
parser = argparse.ArgumentParser(description="Generate music based on provided description.")
parser.add_argument('--description', type=str, required=True, help='Description of the music to generate.')
parser.add_argument('--duration', type=int, default=30, help='Duration of the music in seconds.')
parser.add_argument('--output_name', type=str, default='/content/Audio_Out.wav', help='Output WAV file name.')

# Parse arguments
args = parser.parse_args()

# Generate music with provided arguments
generate_music(args.description, args.duration, args.output_name)


Writing /content/music1.py


In [ ]:
#!pip uninstall audiocraft -y
#!pip install audiocraft

Found existing installation: audiocraft 1.2.0a2
Uninstalling audiocraft-1.2.0a2:
  Successfully uninstalled audiocraft-1.2.0a2
  Using cached audiocraft-1.1.0-py3-none-any.whl
  Using cached hydra_core-1.3.2-py3-none-any.whl (154 kB)
  Using cached spacy-3.5.2-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (6.6 MB)
  Using cached typer-0.7.0-py3-none-any.whl (38 kB)
  Using cached omegaconf-2.3.0-py3-none-any.whl (79 kB)
  Using cached antlr4_python3_runtime-4.9.3-py3-none-any.whl
  Attempting uninstall: antlr4-python3-runtime
    Found existing installation: antlr4-python3-runtime 4.8
    Uninstalling antlr4-python3-runtime-4.8:
      Successfully uninstalled antlr4-python3-runtime-4.8
  Attempting uninstall: typer
    Found existing installation: typer 0.9.0
    Uninstalling typer-0.9.0:
      Successfully uninstalled typer-0.9.0
  Attempting uninstall: omegaconf
    Found existing installation: omegaconf 2.0.6
    Uninstalling omegaconf-2.0.6:
      Successfully uninstal

In [ ]:
!python /content/music1.py --description "scary 160bpm slipknot metal music electric distorted guitar, lead guitar, bass, drums" --duration 30 --output_name "/content/Audio_Out.wav"


2023-12-30 01:45:32.608591: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-12-30 01:45:32.661346: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-30 01:45:32.661396: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-30 01:45:32.663270: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-30 01:45:32.671675: I tensorflow/core/platform/cpu_feature_guar

In [ ]:
%%writefile /content/music4.py
import math
import torchaudio
import torch
import soundfile as sf  # Import the soundfile library
from audiocraft.utils.notebook import display_audio

# Initialize the filename for the first prompt
filename = '/content/Audio_Out.wav'

# Loop to repeat the process 9 times
for i in range(3):
    # Load the audio from the current filename
    prompt_waveform, prompt_sr = torchaudio.load(filename)
    prompt_duration = 2
    prompt_waveform = prompt_waveform[..., :int(prompt_duration * prompt_sr)]

    # Generate the audio continuation
    output = model.generate_continuation(prompt_waveform, prompt_sample_rate=prompt_sr, progress=True, return_tokens=True)
    display_audio(output[0], sample_rate=32000)

    # Move the tensor to CPU, convert to NumPy array, and reshape
    audio_data_cpu = output[0].cpu().numpy().reshape(-1)

    # Generate a new filename for the next iteration
    new_filename = f'/content/Audio_Out{i+2}.wav'

    # Save the audio to the new WAV file
    sf.write(new_filename, audio_data_cpu, 32000)

    if USE_DIFFUSION_DECODER:
        out_diffusion = mbd.tokens_to_wav(output[1])
        display_audio(out_diffusion, sample_rate=32000)
        # Move the tensor to CPU, convert to NumPy array, and reshape
        out_diffusion_cpu = out_diffusion.cpu().numpy().reshape(-1)
        # Save the diffusion decoded audio to a WAV file
        sf.write(f'/content/Audio_Out_Diffusion{i+2}.wav', out_diffusion_cpu, 32000)

    # Update the filename for the next iteration
    filename = new_filename

In [ ]:
!python /content/music4.py

In [ ]:
%%writefile /content/music5.py
import os
import torchaudio

# Initialize an empty tensor to store the concatenated audio
concatenated_waveform = torch.tensor([])

# Loop through the files in the /content/ directory
for i in range(2, 5):  # Assuming you have Audio_Out2.wav, Audio_Out3.wav, Audio_Out4.wav, etc.
    filename = f'/content/Audio_Out{i}.wav'

    # Check if the file exists
    if os.path.exists(filename):
        # Load the audio file
        waveform, sample_rate = torchaudio.load(filename)

        # Concatenate the waveform to the existing concatenated_waveform
        concatenated_waveform = torch.cat((concatenated_waveform, waveform), dim=1)

# Save the concatenated audio as an MP3 file
torchaudio.save('/content/Audio_Out.mp3', concatenated_waveform, sample_rate)

print("Concatenation complete. Saved as Audio_Out.mp3.")

Concatenation complete. Saved as Audio_Out.mp3.


In [ ]:
!python /content/music5.py

# !#!!! Restart Runtime and run Below Cell if you're in trouble


# (TEST) that SDXL / SDV / RemoveBG / TTS / RVC are working

In [ ]:
%cd /content/Wav2Lip
!python inference.py --checkpoint_path checkpoints/wav2lip_gan.pth --face "/content/temp_generated_image.png" --audio "/content/out/daniel_0_0.wav"
%cd /content/

/content/Wav2Lip
Using cuda for inference.
Number of frames available for inference: 1
/content/Wav2Lip/audio.py:100: FutureWarning: Pass sr=16000, n_fft=800 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  return librosa.filters.mel(hp.sample_rate, hp.n_fft, n_mels=hp.num_mels,
(80, 141)
Length of mel chunks: 41
  0% 0/1 [00:00<?, ?it/s]
  0% 0/1 [00:00<?, ?it/s]
100% 1/1 [00:01<00:00,  1.32s/it]
Load checkpoint from: checkpoints/wav2lip_gan.pth
Model loaded
100% 1/1 [00:05<00:00,  5.08s/it]
ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca 

In [ ]:
%cd /content/
!pip install transformers==4.19.0
!python3 /content/tortoise-hf/tortoise-tts/tortoise/do_tts.py --text "house of farts" --voice="dan" --preset high_quality --output="/content/out/"
!mv /content/out/dan_0_0.wav /content/out/daniel_0_0.wav
!python /content/rvcscript.py --model_path "/content/drive/MyDrive/#BACKUPS/#voicervc/Narrator/DBZNarratorENG.pth" --file_index "/content/drive/MyDrive/#BACKUPS/#voicervc/Narrator/added_IVF992_Flat_nprobe_1_DBZNarratorENG_v2.index" --f0_up_key 0
!pip install transformers==4.36.2

/content
/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")
Generating autoregressive samples..
100% 16/16 [00:14<00:00,  1.11it/s]
Computing best candidates using CLVP
100% 16/16 [00:03<00:00,  4.78it/s]
Transforming autoregressive outputs into audio..
100% 400/400 [00:25<00:00, 15.76it/s]
100% 400/400 [00:25<00:00, 15.61it/s]
100% 400/400 [00:25<00:00, 15.68it/s]
2023-12-30 11:31:08.042983: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-12-30 11:31:08.096889: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9

In [ ]:
!pip install transformers==4.36.2

  Using cached transformers-4.36.2-py3-none-any.whl (8.2 MB)
  Using cached tokenizers-0.15.0-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.8 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.12.1
    Uninstalling tokenizers-0.12.1:
      Successfully uninstalled tokenizers-0.12.1
  Attempting uninstall: transformers
    Found existing installation: transformers 4.19.0
    Uninstalling transformers-4.19.0:
      Successfully uninstalled transformers-4.19.0


In [ ]:
import torch
from diffusers import AutoPipelineForText2Image, AutoPipelineForImage2Image

# Initialize the text-to-image pipeline
pipe = AutoPipelineForText2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, variant="fp16").to("cuda")

# Initialize the image-to-image pipeline
image2image_pipe = AutoPipelineForImage2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, use_safetensors=True)
image2image_pipe.enable_model_cpu_offload()


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

In [ ]:
%cd /content/generative-models/
!python /content/loadmod.py
%cd /content/

/content/generative-models
Traceback (most recent call last):
  File "/content/loadmod.py", line 45, in <module>
    model, filter = load_model(
  File "/content/loadmod.py", line 16, in load_model
    config = OmegaConf.load(config)
  File "/usr/local/lib/python3.10/dist-packages/omegaconf/omegaconf.py", line 253, in load
    with io.open(os.path.abspath(file_), "r", encoding="utf-8") as f:
FileNotFoundError: [Errno 2] No such file or directory: '/content/generative-models/generative-models/scripts/sampling/configs/svd_xt.yaml'
/content


In [ ]:
%cd /content/background-replacement-hf
!python /content/background-replacement-hf/removebg.py /content/sdog.png /content/bgremoved.png
%cd /content/

/content/background-replacement-hf
2023-12-30 23:46:03.833244: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-30 23:46:03.833296: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-30 23:46:03.835208: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-30 23:46:05.100508: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Initializing captioner...
config.json: 100% 4.56k/4.56k [00:00<00:00, 19.8MB/s]
pytorch_model.bin: 100% 990M/990M [00:02<00:00, 393MB/s]
tokenizer_config.json: 100% 506/506 [00:00<00:00, 3.42MB/s]
vocab.txt

In [ ]:
%cd /content/background-replacement-hf

/content/background-replacement-hf


In [ ]:
!python /content/fart.py

In [ ]:
%cd /content/

/content


# !#!!!


# !#!!!


# !#!!!


# !#!!!


# !#!!!


# !#!!!


# !#!!!


# !#!!!


# !#!!!


# Old_test_code

In [ ]:
%cd /content/tortoise-hf/src
import sys
sys.path.append('/content/tortoise-hf/src/rvc')
sys.path.append('/content/tortoise-hf/src/rvc-tts-pipe')


/content/tortoise-hf/src


In [ ]:
!python /content/tortoise-hf/src/rvc-tts-pipe/setup.py build

running build


In [ ]:
from rvc_infer import rvc_convert

In [ ]:
%cd /content/tortoise-hf/

/content/tortoise-hf


In [ ]:
%%writefile /content/tortoise-hf/rvcscript.py
import sys
sys.path.append('/content/tortoise-hf/src/rvc')
sys.path.append('/content/tortoise-hf/src/rvc-tts-pipe')
from rvc_infer import rvc_convert
rvc_convert(model_path="/content/#voicervc/Narrator/DBZNarratorENG.pth", file_index="/content/#voicervc/Narrator/added_IVF992_Flat_nprobe_1_DBZNarratorENG_v2.index", f0_up_key=0, input_path="/content/out/daniel_0_0.wav")

Overwriting /content/tortoise-hf/rvcscript.py


In [ ]:
!python /content/tortoise-hf/rvcscript.py

2023-12-28 03:13:21.895665: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-12-28 03:13:21.948660: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-28 03:13:21.948712: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-28 03:13:21.951051: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-28 03:13:21.960313: I tensorflow/core/platform/cpu_feature_guar

In [ ]:
%cd /content/tortoise-hf
!pip install transformers==4.19.0
!python3 /content/tortoise-hf/tortoise-tts/tortoise/do_tts.py --text "please work or ill eat poop" --voice="daniel" --preset high_quality --output="/content/out/"
!python /content/tortoise-hf/rvcscript.py
!pip install transformers==4.36.2

# Tortoise-TTS and RVC

In [ ]:
!python DownTown.py "matt" "https://www.youtube.com/watch?v=BBCl9A9NlRw" "00:05:01 00:05:52" "00:24:33 00:25:00" -k

In [ ]:
!pip install pydub
from pydub import AudioSegment
import os

# Iterate over all mp3 files in the source directory
for filename in os.listdir("/content/#voicemp3"):
    if filename.endswith(".mp3"):
        # Load the MP3 file
        audio_path = os.path.join("/content/#voicemp3", filename)
        audio = AudioSegment.from_mp3(audio_path)

        # Define the duration for each segment in milliseconds (10 seconds = 10000 milliseconds)
        duration_per_segment = 10000

        # Calculate the number of segments
        num_segments = len(audio) // duration_per_segment + (1 if len(audio) % duration_per_segment else 0)

        # Create a new directory for the split files, named after the mp3 file
        new_dir = os.path.join("/content/tortoise-hf/tortoise-tts/tortoise/voices", filename.rsplit(".", 1)[0])
        os.makedirs(new_dir, exist_ok=True)

        # Split the audio and save each segment
        for i in range(num_segments):
            start_time = i * duration_per_segment
            end_time = (i+1) * duration_per_segment
            segment = audio[start_time:end_time]
            segment.export(f"{new_dir}/{i+1}.wav", format="wav")
            print(f"Saved segment {i+1}.wav for {filename}")

print("All segments saved successfully!")


Saved segment 1.wav for matt.mp3
Saved segment 2.wav for matt.mp3
Saved segment 3.wav for matt.mp3
Saved segment 4.wav for matt.mp3
Saved segment 5.wav for matt.mp3
Saved segment 6.wav for matt.mp3
Saved segment 7.wav for matt.mp3
Saved segment 8.wav for matt.mp3
All segments saved successfully!


In [ ]:
!pip uninstall numba numpy llvmlite -y
!pip install numba numpy llvmlite

Found existing installation: numba 0.58.1
Uninstalling numba-0.58.1:
  Successfully uninstalled numba-0.58.1
Found existing installation: numpy 1.23.5
Uninstalling numpy-1.23.5:
  Successfully uninstalled numpy-1.23.5
Found existing installation: llvmlite 0.41.1
Uninstalling llvmlite-0.41.1:
  Successfully uninstalled llvmlite-0.41.1
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 40.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 84.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 MB 38.9 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
lida 0.0.10 requires kaleido, which is not installed.
tensorflow-probability 0.22.0 requires typing-extensions<4.6.0, but you have typing-extensions 4.9.0 which is incompatible.
torchtext 0.16.0 requires torch==2.1.0, but you have torch 2.1.2+cu118

In [ ]:
!pip uninstall numpy -y
!pip install numpy==1.23.5

Found existing installation: numpy 1.23.5
Uninstalling numpy-1.23.5:
  Successfully uninstalled numpy-1.23.5
  Using cached numpy-1.23.5-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.1 MB)


In [ ]:
!pip uninstall tensorflow-probability torchtext -y
!pip install lida tensorflow-probability torchtext kaleido

Found existing installation: tensorflow-probability 0.22.0
Uninstalling tensorflow-probability-0.22.0:
  Successfully uninstalled tensorflow-probability-0.22.0
Found existing installation: torchtext 0.16.0
Uninstalling torchtext-0.16.0:
  Successfully uninstalled torchtext-0.16.0
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 45.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 85.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 MB 20.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 102.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.4/225.4 kB 29.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 90.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.7/51.7 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 107.1 MB/s eta 0:00:00
  Attempting uninstall: torchdata
    Found existing installation: torchdata 0

In [ ]:
%cd /content/tortoise-hf/tortoise-tts
!python setup.py install

/content/tortoise-hf/tortoise-tts
running install
/usr/local/lib/python3.10/dist-packages/setuptools/_distutils/cmd.py:66: SetuptoolsDeprecationWarning: setup.py install is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` directly.
        Instead, use pypa/build, pypa/installer, pypa/build or
        other standards-based tools.

        See https://blog.ganssle.io/articles/2021/10/setup-py-deprecated.html for details.
        ********************************************************************************

!!
  self.initialize_options()
/usr/local/lib/python3.10/dist-packages/setuptools/_distutils/cmd.py:66: EasyInstallDeprecationWarning: easy_install command is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` and ``easy_install``.
        Instead, use pypa/build, pypa/installer, pypa/build 

In [ ]:
!pip install moviepy
%cd /content
!git clone -b dev https://github.com/camenduru/tortoise-hf
%cd /content/tortoise-hf
!git clone -b v1.0 https://github.com/camenduru/tortoise-tts

!pip install gradio scipy -U
%cd /content/tortoise-hf/tortoise-tts
!pip install transformers==4.19.0
!pip install -r requirements.txt
!python setup.py install

%cd /content/

/content
fatal: destination path 'tortoise-hf' already exists and is not an empty directory.
/content/tortoise-hf
fatal: destination path 'tortoise-tts' already exists and is not an empty directory.
  Using cached gradio-4.12.0-py3-none-any.whl (16.6 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 36.4/36.4 MB 45.0 MB/s eta 0:00:00
  Using cached gradio_client-0.8.0-py3-none-any.whl (305 kB)
  Attempting uninstall: scipy
    Found existing installation: scipy 1.9.3
    Uninstalling scipy-1.9.3:
      Successfully uninstalled scipy-1.9.3
  Attempting uninstall: gradio-client
    Found existing installation: gradio_client 0.7.0
    Uninstalling gradio_client-0.7.0:
      Successfully uninstalled gradio_client-0.7.0
  Attempting uninstall: gradio
    Found existing installation: gradio 4.7.1
    Uninstalling gradio-4.7.1:
      Successfully uninstalled gradio-4.7.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour i

  Using cached einops-0.4.1-py3-none-any.whl (28 kB)
  Using cached scipy-1.10.1-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (34.4 MB)
  Using cached numba-0.48.0.tar.gz (2.0 MB)
  Preparing metadata (setup.py) ... done
  Using cached ffmpeg-1.4-py3-none-any.whl
  Using cached numpy-1.20.0.zip (8.0 MB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached llvmlite-0.31.0.tar.gz (110 kB)
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of rotary-embedding-torch to determine which version is compatible with other requirements. This could take a while.
  Using cached rotary_embedding_torch-0.5.2-py3-none-any.whl (5.3 kB)
  Using cached rotary_embedding_torch-0.5.1-py3-none-any.whl (5.2 kB)
  Using cached rotary_embedding_torch-0.5.0-py3-none-any.whl (5.2 kB)
  Using cached rotary_embedding_torch-0.4.0-py3-none-any.whl (5.1 kB)
  Using cached rota

In [ ]:
#!pip3 install --pre torch torchvision torchaudio --index-url https://download.pytorch.org/whl/nightly/cu121
!pip install pyttsx3
!pip install sounddevice
!pip install soundfile
!sudo apt-get update
!sudo apt-get install aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/lj1995/VoiceConversionWebUI/resolve/main/hubert_base.pt -d /content/ -o hubert_base.pt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/lj1995/VoiceConversionWebUI/resolve/main/rmvpe.pt -d /content/ -o rmvpe.pt
!pip install -e git+https://github.com/JarodMica/rvc.git#egg=rvc
!pip install -e git+https://github.com/JarodMica/rvc-tts-pipeline.git#egg=rvc_tts_pipe
import sys
sys.path.append('/content/src/rvc')
sys.path.append('/content/src/rvc-tts-pipe')

Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Hit:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:3 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ Packages [48.6 kB]
Get:4 http://security.ubuntu.com/ubuntu jammy-security InRelease [110 kB]
Hit:5 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:6 https://ppa.launchpadcontent.net/c2d4u.team/c2d4u4.0+/ubuntu jammy InRelease [18.1 kB]
Get:7 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [119 kB]
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Get:10 http://security.ubuntu.com/ubuntu jammy-security/universe amd64 Packages [1,046 kB]
Hit:11 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Get:12 https://ppa.launchpadcontent.net/c2d4u.team/c2d4u4.0+/ubuntu jammy/main Sources [2,254 kB]
Hit:13 http://archi

In [ ]:
%cd /content/tortoise-hf/

/content/tortoise-hf


In [ ]:
!pip install transformers==4.19.0

  Using cached transformers-4.19.0-py3-none-any.whl (4.2 MB)
  Using cached tokenizers-0.12.1-cp310-cp310-manylinux_2_12_x86_64.manylinux2010_x86_64.whl (6.6 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.15.0
    Uninstalling tokenizers-0.15.0:
      Successfully uninstalled tokenizers-0.15.0
  Attempting uninstall: transformers
    Found existing installation: transformers 4.36.2
    Uninstalling transformers-4.36.2:
      Successfully uninstalled transformers-4.36.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
compel 2.0.2 requires transformers~=4.25, but you have transformers 4.19.0 which is incompatible.


In [ ]:
!pip install transformers==4.19.0
!python3 /content/tortoise-hf/tortoise-tts/tortoise/do_tts.py --text "balls fart today in the way" --voice="daniel" --preset high_quality --output="/content/out/"
!pip install transformers==4.36.2

  Using cached transformers-4.19.0-py3-none-any.whl (4.2 MB)
  Using cached tokenizers-0.12.1-cp310-cp310-manylinux_2_12_x86_64.manylinux2010_x86_64.whl (6.6 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.15.0
    Uninstalling tokenizers-0.15.0:
      Successfully uninstalled tokenizers-0.15.0
  Attempting uninstall: transformers
    Found existing installation: transformers 4.36.2
    Uninstalling transformers-4.36.2:
      Successfully uninstalled transformers-4.36.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
compel 2.0.2 requires transformers~=4.25, but you have transformers 4.19.0 which is incompatible.


/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")
Generating autoregressive samples..
100% 16/16 [00:25<00:00,  1.59s/it]
Computing best candidates using CLVP
100% 16/16 [00:03<00:00,  4.72it/s]
Transforming autoregressive outputs into audio..
100% 400/400 [00:22<00:00, 17.86it/s]
100% 400/400 [00:22<00:00, 17.71it/s]
100% 400/400 [00:22<00:00, 17.69it/s]
  Using cached transformers-4.36.2-py3-none-any.whl (8.2 MB)
  Using cached tokenizers-0.15.0-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.8 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.12.1
    Uninstalling tokenizers-0.12.1:
      Successfully uninstalled tokenizers-0.12.1
  Attempting uninstall: transformers
    Found existing i

In [ ]:
import sys
sys.path.append('/content/tortoise-hf/src/rvc')
sys.path.append('/content/tortoise-hf/src/rvc-tts-pipe')

In [ ]:
!python /content/tortoise-hf/src/rvc-tts-pipe/setup.py install

running install
/usr/local/lib/python3.10/dist-packages/setuptools/_distutils/cmd.py:66: SetuptoolsDeprecationWarning: setup.py install is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` directly.
        Instead, use pypa/build, pypa/installer, pypa/build or
        other standards-based tools.

        See https://blog.ganssle.io/articles/2021/10/setup-py-deprecated.html for details.
        ********************************************************************************

!!
  self.initialize_options()
/usr/local/lib/python3.10/dist-packages/setuptools/_distutils/cmd.py:66: EasyInstallDeprecationWarning: easy_install command is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` and ``easy_install``.
        Instead, use pypa/build, pypa/installer, pypa/build or
        other standards-based t

In [ ]:
!pip install torch==1.13.1 torchdata==0.5.1 torchaudio==0.13.1 torchvision==0.14.1+cu117

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 887.5/887.5 MB 1.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.6/4.6 MB 98.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.2/4.2 MB 96.5 MB/s eta 0:00:00
ERROR: Could not find a version that satisfies the requirement torchvision==0.14.1+cu117 (from versions: 0.1.6, 0.1.7, 0.1.8, 0.1.9, 0.2.0, 0.2.1, 0.2.2, 0.2.2.post2, 0.2.2.post3, 0.12.0, 0.13.0, 0.13.1, 0.14.0, 0.14.1, 0.15.0, 0.15.1, 0.15.2, 0.16.0, 0.16.1, 0.16.2)
ERROR: No matching distribution found for torchvision==0.14.1+cu117


In [ ]:
#!pip install omegaconf==2.0.5
!pip install antlr4-python3-runtime==4.8

  Using cached antlr4_python3_runtime-4.8-py3-none-any.whl
  Attempting uninstall: antlr4-python3-runtime
    Found existing installation: antlr4-python3-runtime 4.9.3
    Uninstalling antlr4-python3-runtime-4.9.3:
      Successfully uninstalled antlr4-python3-runtime-4.9.3


In [ ]:
!pip uninstall xFormers -y
!pip install xformers

Found existing installation: xformers 0.0.23.post1
Uninstalling xformers-0.0.23.post1:
  Successfully uninstalled xformers-0.0.23.post1
  Using cached xformers-0.0.23.post1-cp310-cp310-manylinux2014_x86_64.whl (213.0 MB)
  Using cached torch-2.1.2-cp310-cp310-manylinux1_x86_64.whl (670.2 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.2/89.2 MB 19.2 MB/s eta 0:00:00
  Attempting uninstall: triton
    Found existing installation: triton 2.0.0
    Uninstalling triton-2.0.0:
      Successfully uninstalled triton-2.0.0
  Attempting uninstall: torch
    Found existing installation: torch 2.0.1
    Uninstalling torch-2.0.1:
      Successfully uninstalled torch-2.0.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchdata 0.6.1 requires torch==2.0.1, but you have torch 2.1.2 which is incompatible.
torchtext 0.16.2+cpu requires torchdata==0.7.1, but you have tor

In [ ]:
import sys
sys.path.append('/content/tortoise-hf/src/rvc')
sys.path.append('/content/tortoise-hf/src/rvc-tts-pipe')
from rvc_infer import rvc_convert

In [ ]:
%%writefile test.py

import argparse
import os
import time
import shutil  # Added this import for copying files
from rvc_infer import rvc_convert  # Assuming the rvc_infer module is available

def copy_output_file(src, dest):
    try:
        shutil.copy(src, dest)
        print(f"File copied from {src} to {dest}")
    except Exception as e:
        print(f"An error occurred while copying: {e}")

if __name__ == "__main__":
    parser = argparse.ArgumentParser()
    parser.add_argument("--model_path", required=True)
    parser.add_argument("--file_index", required=True)
    parser.add_argument("--f0_up_key", required=True)
    parser.add_argument("--input_path", required=True)
    parser.add_argument("--out", required=True)
    args = parser.parse_args()

    # Call rvc_convert function
    rvc_convert(model_path=args.model_path, file_index=args.file_index, f0_up_key=int(args.f0_up_key), input_path=args.input_path)

    # Wait for 3 seconds to ensure the output file is ready
    time.sleep(0.25)

    # Copy file
    default_output_path = "/content/output/out.wav"
    copy_output_file(default_output_path, args.out)


Writing test.py


In [ ]:
%%writefile DownTown.py
import os
import argparse
from yt_dlp import YoutubeDL
from moviepy.editor import VideoFileClip, concatenate_videoclips

# Create directories if they don't exist
if not os.path.exists('/content/vids'):
    os.makedirs('/content/vids')

if not os.path.exists('/content/#voicemp3'):
    os.makedirs('/content/#voicemp3')

# Function to download a video segment
def download_segment(start, end, index, video_url):
    ydl_opts = {
        'format': 'best',  # changed from '22' to 'best'
        'outtmpl': f'/content/vids/segment_{index}.mp4',
        'external_downloader': 'ffmpeg',
        'external_downloader_args': ['-ss', start, '-to', end]
    }

    with YoutubeDL(ydl_opts) as ydl:
        ydl.download([video_url])


# Command-line argument parsing
def main():
    parser = argparse.ArgumentParser(description="Download video segments, concatenate, and extract audio.")
    parser.add_argument("name", help="Name for the final video and audio files")
    parser.add_argument("video_url", help="URL of the YouTube video")
    parser.add_argument("timestamps", nargs="+", help="List of timestamps in the format 'start end'")
    parser.add_argument("-v", "--remove-video", action="store_true", help="Remove video file at the end")
    parser.add_argument("-a", "--remove-audio", action="store_true", help="Remove audio file at the end")
    parser.add_argument("-k", "--keep-both", action="store_true", help="Keep both audio and video files")

    args = parser.parse_args()
    name = args.name
    video_url = args.video_url
    timestamps = [tuple(timestamp.split()) for timestamp in args.timestamps]

    # Download each segment
    for i, (start_time, end_time) in enumerate(timestamps):
        download_segment(start_time, end_time, i, video_url)

    # Combine the segments
    segments = [VideoFileClip(f'/content/vids/segment_{i}.mp4') for i in range(len(timestamps))]
    final_clip = concatenate_videoclips(segments)
    final_clip.write_videofile(f"/content/vids/{name}.mp4")

    # Extract audio and save as MP3
    audio = final_clip.audio.set_fps(44100)
    audio.write_audiofile(f"/content/#voicemp3/{name}.mp3")

    # Clean up segment files
    for i in range(len(timestamps)):
        os.remove(f'/content/vids/segment_{i}.mp4')

    # Remove video and/or audio files if specified
    if args.remove_video and not args.keep_both:
        os.remove(f'/content/vids/{name}.mp4')
    if args.remove_audio and not args.keep_both:
        os.remove(f'/content/#voicemp3/{name}.mp3')

if __name__ == "__main__":
    main()


Writing DownTown.py


In [ ]:
%%writefile RVC-dl.py
import requests
import zipfile
import io
import os
import sys
import re
import gdown

def resolve_hugging_face_url(zip_url):
    response = requests.head(zip_url, allow_redirects=True)
    if response.status_code == 200:
        return response.url
    else:
        return None

def extract_google_drive(file_id, target_directory):
    temp_zip_path = "/content/temp_google_drive.zip"
    gdown.download(f"https://drive.google.com/uc?id={file_id}", temp_zip_path, quiet=False)

    with zipfile.ZipFile(temp_zip_path, 'r') as zip_ref:
        for file_info in zip_ref.infolist():
            if not file_info.is_dir():  # Only extract files
                file_info.filename = os.path.basename(file_info.filename)
                zip_ref.extract(file_info, target_directory)

    os.remove(temp_zip_path)
    print("ZIP file downloaded and extracted successfully from Google Drive.")

def extract_zip(zip_url, target_directory):
    os.makedirs(target_directory, exist_ok=True)

    if "drive.google.com" in zip_url:
        file_id_search = re.search(r"/file/d/([a-zA-Z0-9_-]+)/", zip_url)
        if file_id_search:
            file_id = file_id_search.group(1)
            extract_google_drive(file_id, target_directory)
        else:
            print("Invalid Google Drive URL.")
        return

    if "huggingface.co" in zip_url:
        zip_url = resolve_hugging_face_url(zip_url)
        if zip_url is None:
            print("Failed to resolve Hugging Face URL.")
            return

    response = requests.get(zip_url)
    if response.status_code == 200:
        with zipfile.ZipFile(io.BytesIO(response.content), 'r') as zip_ref:
            for file_info in zip_ref.infolist():
                if not file_info.is_dir():  # Only extract files
                    file_info.filename = os.path.basename(file_info.filename)
                    zip_ref.extract(file_info, target_directory)
        print("ZIP file downloaded and extracted successfully.")
    else:
        print("Failed to download ZIP file.")

if __name__ == "__main__":
    if len(sys.argv) != 3:
        print("Usage: python RVC-dl.py <target_directory> <zip_url>")
    else:
        target_directory = sys.argv[1]
        zip_url = sys.argv[2]
        extract_zip(zip_url, target_directory)


Writing RVC-dl.py


In [ ]:
!pip install gdown

In [ ]:
!python RVC-dl.py "/content/#voicervc/Narrator/" "https://huggingface.co/SyberGen/DragonBallVModels/resolve/main/DBZNarratorENG.zip"


ZIP file downloaded and extracted successfully.


In [ ]:
!python DownTown.py "matt" "https://www.youtube.com/watch?v=BBCl9A9NlRw" "00:05:01 00:05:52" "00:24:33 00:25:00" -k

In [ ]:
!pip install pydub
from pydub import AudioSegment
import os

# Iterate over all mp3 files in the source directory
for filename in os.listdir("/content/#voicemp3"):
    if filename.endswith(".mp3"):
        # Load the MP3 file
        audio_path = os.path.join("/content/#voicemp3", filename)
        audio = AudioSegment.from_mp3(audio_path)

        # Define the duration for each segment in milliseconds (10 seconds = 10000 milliseconds)
        duration_per_segment = 10000

        # Calculate the number of segments
        num_segments = len(audio) // duration_per_segment + (1 if len(audio) % duration_per_segment else 0)

        # Create a new directory for the split files, named after the mp3 file
        new_dir = os.path.join("/content/tortoise-hf/tortoise-tts/tortoise/voices", filename.rsplit(".", 1)[0])
        os.makedirs(new_dir, exist_ok=True)

        # Split the audio and save each segment
        for i in range(num_segments):
            start_time = i * duration_per_segment
            end_time = (i+1) * duration_per_segment
            segment = audio[start_time:end_time]
            segment.export(f"{new_dir}/{i+1}.wav", format="wav")
            print(f"Saved segment {i+1}.wav for {filename}")

print("All segments saved successfully!")


Saved segment 1.wav for matt.mp3
Saved segment 2.wav for matt.mp3
Saved segment 3.wav for matt.mp3
Saved segment 4.wav for matt.mp3
Saved segment 5.wav for matt.mp3
Saved segment 6.wav for matt.mp3
Saved segment 7.wav for matt.mp3
Saved segment 8.wav for matt.mp3
All segments saved successfully!


In [ ]:
!python "/content/tortoise-hf/test.py" --model_path="/content/#voicervc/Narrator/DBZNarratorENG.pth" --file_index="/content/#voicervc/Narrator/added_IVF992_Flat_nprobe_1_DBZNarratorENG_v2.index" --f0_up_key=0 --input_path="/content/out/daniel_0_0.wav" --out="/content/output/worked.wav"


2023-12-28 00:18:30.569726: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-28 00:18:30.569776: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-28 00:18:30.571991: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-28 00:18:31.766182: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Traceback (most recent call last):
  File "/content/tortoise-hf/test.py", line 6, in <module>
    from rvc_infer import rvc_convert  # Assuming the rvc_infer module is available
  File "/content/tortoise-hf/src/rvc-tts-pipe/rvc_infer.py", li

# wav2lip

In [ ]:
%cd /content/

/content


In [ ]:
#!pip install -q torch==1.13.1+cu116 torchvision==0.14.1+cu116 torchaudio==0.13.1 torchtext==0.14.1 torchdata==0.5.1 --extra-index-url https://download.pytorch.org/whl/cu116 -U

# Navigate to /content/ directory
%cd /content/

!git clone https://huggingface.co/camenduru/Wav2Lip
!pip install gradio yt_dlp ffmpeg-python librosa==0.8.0

# Change directory to Wav2Lip
%cd Wav2Lip

# AnimateDiff

In [ ]:
%cd /content
!git clone -b dev https://github.com/camenduru/LongAnimateDiff-hf
%cd /content/LongAnimateDiff-hf

!pip install -q omegaconf diffusers[torch]==0.11.1 einops accelerate gradio==3.50.2
!pip install -q https://download.pytorch.org/whl/cu121/xformers-0.0.22.post7-cp310-cp310-manylinux2014_x86_64.whl

!apt -y install -qq aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/DreamBooth_LoRA/epiCRealismNaturalSin.safetensors -d /content/LongAnimateDiff-hf/models/DreamBooth_LoRA -o epiCRealismNaturalSin.safetensors
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/DreamBooth_LoRA/toonyou_beta3.safetensors -d /content/LongAnimateDiff-hf/models/DreamBooth_LoRA -o toonyou_beta3.safetensors
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/Motion_Module/lt_long_mm_16_64_frames.ckpt -d /content/LongAnimateDiff-hf/models/Motion_Module -o lt_long_mm_16_64_frames.ckpt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/Motion_Module/lt_long_mm_32_frames.ckpt -d /content/LongAnimateDiff-hf/models/Motion_Module -o lt_long_mm_32_frames.ckpt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/StableDiffusion/stable-diffusion-v1-5/safety_checker/pytorch_model.bin -d /content/LongAnimateDiff-hf/models/StableDiffusion/stable-diffusion-v1-5/safety_checker -o pytorch_model.bin
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/StableDiffusion/stable-diffusion-v1-5/text_encoder/pytorch_model.bin -d /content/LongAnimateDiff-hf/models/StableDiffusion/stable-diffusion-v1-5/text_encoder -o pytorch_model.bin
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/StableDiffusion/stable-diffusion-v1-5/unet/diffusion_pytorch_model.bin -d /content/LongAnimateDiff-hf/models/StableDiffusion/stable-diffusion-v1-5/unet -o diffusion_pytorch_model.bin
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/spaces/Lightricks/LongAnimateDiff/resolve/main/models/StableDiffusion/stable-diffusion-v1-5/vae/diffusion_pytorch_model.bin -d /content/LongAnimateDiff-hf/models/StableDiffusion/stable-diffusion-v1-5/vae -o diffusion_pytorch_model.bin

!python app.py

/content
Cloning into 'LongAnimateDiff-hf'...
remote: Enumerating objects: 123, done.
remote: Counting objects: 100% (123/123), done.
remote: Compressing objects: 100% (86/86), done.
remote: Total 123 (delta 38), reused 111 (delta 32), pack-reused 0
Receiving objects: 100% (123/123), 571.43 KiB | 19.05 MiB/s, done.
Resolving deltas: 100% (38/38), done.
Error downloading object: models/DreamBooth_LoRA/epiCRealismNaturalSin.safetensors (84d76a0): Smudge error: Error downloading models/DreamBooth_LoRA/epiCRealismNaturalSin.safetensors (84d76a0328ee5a1a2a1d466ba7478ab59183e3fea385441528aa4c5d567fd43e): [84d76a0328ee5a1a2a1d466ba7478ab59183e3fea385441528aa4c5d567fd43e] Object does not exist on the server: [404] Object does not exist on the server

Errors logged to /content/LongAnimateDiff-hf/.git/lfs/logs/20231227T052604.47999347.log
Use `git lfs logs last` to view the log.
error: external filter 'git-lfs filter-process' failed
fatal: models/DreamBooth_LoRA/epiCRealismNaturalSin.safetensors

# HELP!!! / You in Trouble?

## RemoveBG Fix

In [ ]:
!pip install -r /content/background-replacement-hf/requirements.txt

## LOAD Diffusers for stabilityai/stable-diffusion-xl-base-1.0

In [ ]:
import torch
from diffusers import AutoPipelineForText2Image, AutoPipelineForImage2Image

# Initialize the text-to-image pipeline
pipe = AutoPipelineForText2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, variant="fp16").to("cuda")

# Initialize the image-to-image pipeline
image2image_pipe = AutoPipelineForImage2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, use_safetensors=True)
image2image_pipe.enable_model_cpu_offload()


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

## Unload SDXL from GPU Memory

In [ ]:
torch.cuda.empty_cache()
!nvidia-smi #just to check if above code did anything

Wed Dec 27 05:25:04 2023       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA A100-SXM4-40GB          Off | 00000000:00:04.0 Off |                    0 |
| N/A   35C    P0              51W / 400W |    423MiB / 40960MiB |      0%      Default |
|                                         |                      |             Disabled |
+-----------------------------------------+----------------------+--

## LOAD SDV-MODEL

In [ ]:
%cd /content/generative-models
!python /content/loadmod.py
%cd /content/

/content/generative-models
Traceback (most recent call last):
  File "/content/loadmod.py", line 45, in <module>
    model, filter = load_model(
  File "/content/loadmod.py", line 16, in load_model
    config = OmegaConf.load(config)
  File "/usr/local/lib/python3.10/dist-packages/omegaconf/omegaconf.py", line 253, in load
    with io.open(os.path.abspath(file_), "r", encoding="utf-8") as f:
FileNotFoundError: [Errno 2] No such file or directory: '/content/generative-models/generative-models/scripts/sampling/configs/svd_xt.yaml'
/content


## Reset Diffusers and Dependancies

In [ ]:
!pip uninstall -r /content/unofficial-SDXL-Turbo-i2i-t2i/requirements.txt -y
!pip install -r /content/unofficial-SDXL-Turbo-i2i-t2i/requirements.txt

Found existing installation: diffusers 0.23.1
Uninstalling diffusers-0.23.1:
  Successfully uninstalled diffusers-0.23.1
Found existing installation: transformers 4.36.2
Uninstalling transformers-4.36.2:
  Successfully uninstalled transformers-4.36.2
Found existing installation: gradio 4.7.1
Uninstalling gradio-4.7.1:
  Successfully uninstalled gradio-4.7.1
Found existing installation: torch 2.1.2
Uninstalling torch-2.1.2:
  Successfully uninstalled torch-2.1.2
Found existing installation: fastapi 0.104.0
Uninstalling fastapi-0.104.0:
  Successfully uninstalled fastapi-0.104.0
Found existing installation: uvicorn 0.23.2
Uninstalling uvicorn-0.23.2:
  Successfully uninstalled uvicorn-0.23.2
Found existing installation: Pillow 10.1.0
Uninstalling Pillow-10.1.0:
  Successfully uninstalled Pillow-10.1.0
Found existing installation: accelerate 0.24.0
Uninstalling accelerate-0.24.0:
  Successfully uninstalled accelerate-0.24.0
Found existing installation: compel 2.0.2
Uninstalling compel-2.0

In [ ]:
!pip uninstall Diffusers -y
!pip install Diffusers

Found existing installation: diffusers 0.23.1
Uninstalling diffusers-0.23.1:
  Successfully uninstalled diffusers-0.23.1
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 21.3 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
compel 2.0.2 requires transformers~=4.25, but you have transformers 4.19.0 which is incompatible.


## Reset torch n transformers

In [ ]:
!pip uninstall torch torchtext torchdata torchvision torchaudio torchmetrics -y
!pip install torch torchtext torchdata torchvision torchaudio torchmetrics --index-url https://download.pytorch.org/whl/cu118

Found existing installation: torch 2.0.1+cu118
Uninstalling torch-2.0.1+cu118:
  Successfully uninstalled torch-2.0.1+cu118
Found existing installation: torchtext 0.16.0
Uninstalling torchtext-0.16.0:
  Successfully uninstalled torchtext-0.16.0
Found existing installation: torchdata 0.6.1
Uninstalling torchdata-0.6.1:
  Successfully uninstalled torchdata-0.6.1
Found existing installation: torchvision 0.15.2+cu118
Uninstalling torchvision-0.15.2+cu118:
  Successfully uninstalled torchvision-0.15.2+cu118
Found existing installation: torchaudio 2.0.2+cu118
Uninstalling torchaudio-2.0.2+cu118:
  Successfully uninstalled torchaudio-2.0.2+cu118
Found existing installation: torchmetrics 1.2.1
Uninstalling torchmetrics-1.2.1:
  Successfully uninstalled torchmetrics-1.2.1
Looking in indexes: https://download.pytorch.org/whl/cu118
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 GB 861.8 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 84.6 MB/s eta 0:00:00
     ━━━

In [ ]:
!pip uninstall xformers transformers -y
!pip install xformers transformers

Found existing installation: xformers 0.0.22
Uninstalling xformers-0.0.22:
  Successfully uninstalled xformers-0.0.22
Found existing installation: transformers 4.19.0
Uninstalling transformers-4.19.0:
  Successfully uninstalled transformers-4.19.0
  Using cached xformers-0.0.23.post1-cp310-cp310-manylinux2014_x86_64.whl (213.0 MB)
  Using cached transformers-4.36.2-py3-none-any.whl (8.2 MB)
  Using cached tokenizers-0.15.0-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.8 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.12.1
    Uninstalling tokenizers-0.12.1:
      Successfully uninstalled tokenizers-0.12.1


# TEST if removeBG sdxl and SDV are working

In [ ]:
%cd /content/background-replacement-hf
import subprocess
output_image_path = "/content/bgremoved.png"
temp_image_path = "/content/temp_generated_image.png"
subprocess.run(["python", "/content/background-replacement-hf/removebg.py", temp_image_path, output_image_path], capture_output=True, text=True)
%cd /content/

/content/background-replacement-hf
/content


In [ ]:
import torch
from diffusers import AutoPipelineForText2Image, AutoPipelineForImage2Image

# Initialize the text-to-image pipeline
pipe = AutoPipelineForText2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, variant="fp16").to("cuda")

# Initialize the image-to-image pipeline
image2image_pipe = AutoPipelineForImage2Image.from_pretrained("stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, use_safetensors=True)
image2image_pipe.enable_model_cpu_offload()


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

In [ ]:
%cd /content/generative-models
!python /content/loadmod.py

/content/generative-models
Traceback (most recent call last):
  File "/content/loadmod.py", line 45, in <module>
    model, filter = load_model(
  File "/content/loadmod.py", line 16, in load_model
    config = OmegaConf.load(config)
  File "/usr/local/lib/python3.10/dist-packages/omegaconf/omegaconf.py", line 253, in load
    with io.open(os.path.abspath(file_), "r", encoding="utf-8") as f:
FileNotFoundError: [Errno 2] No such file or directory: '/content/generative-models/generative-models/scripts/sampling/configs/svd_xt.yaml'
